In [62]:
import pickle
import os
import json
from copy import deepcopy
import pandas as pd
import csv
from datetime import datetime, timedelta
from collections import Counter
import numpy as np

In [63]:
path =os.path.expanduser('/Users/fan/Desktop/Fullhouse/WCM/HospitalManagement/OrderAnalysis-master/')
path = '/Users/fan/Desktop/Fullhouse/WCM/HospitalManagement/OrderAnalysis-master/'

In [64]:
#fh = open(path + "2_EDDC_HF_2012_2018_ouput_0305.json", 'r')
fh = open(path + "2_EDDC_HF_2012_2018_ouput_cv3_notcancelled.json", 'r')
data3 = json.load(fh)

In [65]:
len(data3)

2291

In [66]:
data = deepcopy(data3)

add eligibility

In [67]:
for pid in data3:
    if data3[pid]['age']==-1:
        print(pid,data3[pid]['clientID'])

801960800270 100054900200
807698500270 201961400200
808452000270 136876900200
830656200270 213516200200
831102500270 135848900200
846098500270 207939000200
851791700270 220590700200
862807400270 211244200200
864469800270 223704000200
867586500270 201961400200
870038000270 225127500200
871675700270 158488900200
878255600270 235189400200
891718700270 230635000200
895196700270 124830400200
903498900270 124830400200
906847700270 135848900200
907928100270 201961400200
915646200270 218835200200
917053700270 236283000200
920127000270 235946200200
934558300270 238761700200
937053600270 47833300200
957709800270 135848900200
962215600270 225965700200
969390400270 183749400200
977318000270 244922200200
977802600270 180313100200
1000484400270 142409700200
1002274900270 156074700200
1003920400270 205177900200
1031224000270 47833300200
1038101400270 135848900200
1038270600270 158488900200
1043351200270 60311300200
1056478000270 60311300200
1057616600270 234852800200
1063223500270 246066700200
106540

In [68]:
eligible=[]
c=0
c2=0
for pid in data3:
#     print(pid)
#     print(data3[pid]['age'])
    if len(data3[pid]['appt'])>1 and data3[pid]['service']=='MED':
        for date in sorted(data3[pid]['appt'],reverse=True):
            age=int(date[0:4])-data3[pid]['age']
            if age>18 and age<90:
                eligible.append(pid)
            elif data3[pid]['age']<0:
                c2+=1 #age limit  
            elif age>=90:
                c=c+1 #no age info
            break
print(len(eligible),c2,c)  ## 55 people don't have age, 400 people age >=90 or <=18

1651 55 400


In [69]:
for pid in data3:
    if pid in eligible:
        pass
    else:
        del data[pid]

In [70]:
len(data)

1651

In [8]:
c=0
for pid in data2:
    if data2[pid]['dischargedisposition'] =='PATIENT EXPIRED':
        c=c+1
print(c)

NameError: name 'data2' is not defined

In [ ]:
1412/1651

see some dates below have 0 locations

In [71]:
locationpid={}
for pid in data:
    locationpid[pid]=[]
    for date in data3[pid]['appt']:
        if len(data3[pid]['appt'][date]['location'])>0:
            locationpid[pid].append(str(list(set(data3[pid]['appt'][date]['location']))).split('[')[1].split('-')[0].split(']')[0])
for pid in locationpid:
    locationpid[pid]=list(set(locationpid[pid]))

In [72]:
locationpid

{'556943700270': ["'ED AREA C'", "'G04N", "'Adult ED'", "'G04S"],
 '561002000270': ["'ED AREA A'", "'G05S", "'Adult ED'"],
 '562000000270': ["'ED AREA C'",
  "'L4 ",
  "'Adult ED'",
  "'EDIB",
  "'G05C",
  "'Cornell Interv. Cardiology'",
  "'G04N"],
 '567313100270': ["'L4 ",
  "'G05S",
  "'G10N",
  "'Adult ED'",
  "'G04S",
  "'EDIA",
  "'G05C",
  "'ED AREA A'",
  "'G04N"],
 '579333200270': ["'ED AREA A'", "'G02N", "'Adult ED'", "'EDIA"],
 '582002300270': ["'ED AREA C'", "'Adult ED'", "'G05N", "'EDIA", "'G05W"],
 '584744300270': ["'G04N", "'G04S"],
 '608150700270': ["'LMH4C", "'LMH", "'LMH ED QR'"],
 '624731800270': ["'LMH ED", "'Cornell Interv. Cardiology'", "'LMH", "'G14S"],
 '624817200270': ["'G05S", "'Adult ED'", "'G04S", "'G05N", "'ED AREA A'"],
 '653284000270': ["'ED AREA C'", "'Adult ED'", "'EDIC"],
 '684111000270': ["'ED AREA C'", "'G05S", "'Adult ED'"],
 '685155700270': ["'G05N", "'G05S", "'EDIA", "'G05C"],
 '685526500270': ["'ED AREA C'", "'G05N", "'Adult ED'", "'G04S"],
 '737

In [73]:
clientguid=[]
for pid in data:
    if data[pid]['clientID'] not in clientguid and pid in eligible:
        clientguid.append(data[pid]['clientID'])
print(len(clientguid))

1356


compute outcome measures for 30, 60, 90 day readmissions

In [74]:
readmission={}
readmissionvisitguids30=[]
readmissionvisitguids60=[]
readmissionvisitguids90=[]
c=0
s=0
r=0
for guid in clientguid:
    readmission[guid]=[]
for guid in clientguid:
    for pid in data:
        if int(guid)==int(data[pid]['clientID']):
            readmission[guid].append([data[pid]['admittime'],data[pid]['dischargetime'],pid])
            r=r+1
print("num unique pt guids",len(readmission))  
print("num visits",len(data))
l=0
a=0
b=0
for guid in readmission:
    if len(readmission[guid])>1:
        l=l+1
for guid in readmission:
    for i in range(len(readmission[guid])-1):
        s=s+1
        if (datetime.strptime(readmission[guid][i+1][0],'%Y-%m-%d %H:%M:%S')-datetime.strptime(readmission[guid][i][1],'%Y-%m-%d %H:%M:%S')).days>=30:
            c=c+1
        else:
            readmissionvisitguids30.append(readmission[guid][i+1][2])
            
        if (datetime.strptime(readmission[guid][i+1][0],'%Y-%m-%d %H:%M:%S')-datetime.strptime(readmission[guid][i][1],'%Y-%m-%d %H:%M:%S')).days<60:
            readmissionvisitguids60.append(readmission[guid][i+1][2])
        if (datetime.strptime(readmission[guid][i+1][0],'%Y-%m-%d %H:%M:%S')-datetime.strptime(readmission[guid][i][1],'%Y-%m-%d %H:%M:%S')).days<90:
            readmissionvisitguids90.append(readmission[guid][i+1][2])
        
readmissionvisitguids30=list(set(readmissionvisitguids30))
print("num unique pt guids with more than 1 admission",l)
print("num readmissions",s)
print("num re-admissions that are NOT 30-day",c)
print("num re-admissions that are 30-day",len(readmissionvisitguids30))
print("num re-admissions that are 60-day",len(readmissionvisitguids60))
print("num re-admissions that are 90-day",len(readmissionvisitguids90))

num unique pt guids 1356
num visits 1651
num unique pt guids with more than 1 admission 219
num readmissions 295
num re-admissions that are NOT 30-day 243
num re-admissions that are 30-day 52
num re-admissions that are 60-day 86
num re-admissions that are 90-day 121


In [75]:
for pid in data:
    data[pid]['30day_readmit']=0
    data[pid]['60day_readmit']=0
    data[pid]['90day_readmit']=0
    data[pid]['LOS']=(datetime.strptime(data[pid]['dischargetime'],'%Y-%m-%d %H:%M:%S') - datetime.strptime(data[pid]['admittime'], '%Y-%m-%d %H:%M:%S')).days
    if pid in readmissionvisitguids30:
        data[pid]['30day_readmit']=1
    if pid in readmissionvisitguids60:
        data[pid]['60day_readmit']=1
    if pid in readmissionvisitguids90:
        data[pid]['90day_readmit']=1

In [76]:
for pid in data:
    print(pid,'@', data[pid]['sex'],'@',data[pid]['marry'],'@', data[pid]['language'],'@',data[pid]['ethnicity'],'@',data[pid]['race'])

556943700270 @ Male @ Married @ Spanish @ H @ Other Not Described
561002000270 @ Male @ Married @ English @ N @ Other Not Described
562000000270 @ Male @ Divorced @ English @ N @ Other Not Described
567313100270 @ Male @ Married @ German @ N @ Other Not Described
579333200270 @ Female @ Single @ English @ D @ Declined
582002300270 @ Female @ Married @ English @ N @ Black/African Am.
584744300270 @ Male @ Widower @ Unknown @ U @ White
608150700270 @ Male @ Single @ English @ N @ White
624731800270 @ Male @ Married @ English @ N @ Other Not Described
624817200270 @ Male @ Married @ English @ N @ Other Not Described
653284000270 @ Female @ Single @ Unknown @ U @ Declined
684111000270 @ Male @ Married @ English @ H @ White
685155700270 @ Female @ Married @ English @ N @ White
685526500270 @ Male @ Single @ English @ U @ Black/African Am.
737643900270 @ Male @ Divorced @ English @ H @ Declined
763338100270 @ Male @ Single @ English @ U @ Other Not Described
763976700270 @ Female @ Widower @

835085600270 @ Female @ Widower @ Spanish @ U @ Other Not Described
835209400270 @ Female @ Single @ Cantonese @ N @ Asian
835270600270 @ Male @ Married @ English @ U @ White
835546300270 @ Male @ Single @ Chinese @ N @ Asian
835593900270 @ Female @ Divorced @ English @ N @ White
836107700270 @ Female @ Married @ English @ N @ Declined
836622300270 @ Female @ Married @ English @ N @ White
836629800270 @ Male @ Single @ English @ N @ White
836902300270 @ Male @ Married @ English @ N @ White
837381700270 @ Male @ Married @ English @ N @ White
837601100270 @ Female @ Widower @ English @ N @ White
837648200270 @ Male @ Married @ English @ U @ Declined
838254600270 @ Male @ Married @ English @ U @ Declined
839433500270 @ Female @ Single @ English @ N @ White
841042900270 @ Male @ Married @ Cantonese @ N @ Asian
841081100270 @ Female @ Widower @ English @ N @ White
841145400270 @ Male @ Married @ English @ U @ White
841169800270 @ Female @ Single @ English @ N @ White
841197100270 @ Male @ M

904594600270 @ Female @ Single @ English @ N @ White
904707500270 @ Male @ Single @ English @ N @ Black/African Am.
905323500270 @ Female @ Widower @ English @ U @ Asian
905325700270 @ Male @ Married @ English @ N @ White
905380100270 @ Male @ Married @ English @ N @ Asian
905516700270 @ Male @ Single @ Spanish @ H @ Other Not Described
905557100270 @ Female @ Divorced @ English @ N @ Black/African Am.
905600000270 @ Male @ Single @ English @ N @ Declined
905679600270 @ Male @ Married @ English @ N @ White
905688800270 @ Male @ Single @ English @ N @ White
905784800270 @ Male @ Married @ English @ N @ White
906228800270 @ Female @ Single @ English @ N @ White
907005400270 @ Male @ Married @ English @ N @ White
907705000270 @ Female @ Married @ English @ N @ White
907771400270 @ Male @ Married @ English @ N @ White
908102800270 @ Male @ Married @ Cantonese @ U @ Asian
908207800270 @ Female @ Widower @ English @ N @ Asian
908234400270 @ Male @ Single @ English @ H @ Other Not Described
9

957496000270 @ Male @ Married @ English @ N @ Black/African Am.
957513100270 @ Male @ Single @ English @ N @ Black/African Am.
957757700270 @ Male @ Married @ English @ U @ White
957922600270 @ Female @ Married @ English @ N @ Declined
958079200270 @ Female @ Divorced @ English @ N @ Black/African Am.
958587900270 @ Male @ Single @ English @ U @ Other Not Described
958617600270 @ Female @ Single @ Spanish @ HM @ Other Not Described
959054100270 @ Female @ Widower @ English @ D @ White
959336500270 @ Male @ Married @ Cantonese @ N @ Asian
959418200270 @ Male @ Single @ Chinese @ N @ Asian
960374400270 @ Male @ Married @ English @ U @ Unknown-Pt not Avail
960413000270 @ Female @ Widower @ Spanish @ HM @ Other Not Described
960618800270 @ Male @ Married @ Albanian @ N @ White
960741400270 @ Female @ Single @ Chinese @ N @ Asian
960829800270 @ Male @ Single @ English @ H @ White
961312600270 @ Male @ Married @ English @ N @ White
961340100270 @ Male @ Married @ English @ N @ White
96193640

1006778700270 @ Female @ Divorced @ English @ N @ White
1007524400270 @ Female @ Separated @ English @ N @ Black/African Am.
1008310400270 @ Male @ Married @ Mandarin @ N @ Asian
1008374100270 @ Female @ Single @ English @ N @ Black/African Am.
1008380900270 @ Male @ Single @ English @ N @ Black/African Am.
1008405700270 @ Female @ Single @ English @ N @ Black/African Am.
1008436800270 @ Female @ M @ SPA @ H @ O
1008487300270 @ Male @ M @ ENG @ N @ W
1008760100270 @ Male @ Separated @ English @ N @ White
1010063700270 @ Male @ Divorced @ English @ N @ Black/African Am.
1011065500270 @ Male @ Widower @ English @ N @ Black/African Am.
1011151100270 @ Male @ Married @ English @ U @ Unknown-Pt not Avail
1011331400270 @ Male @ M @ ENG @ N @ B
1011739000270 @ Female @ Single @ English @ U @ Declined
1011810500270 @ Male @ Married @ English @ N @ Asian
1012091300270 @ Female @ Single @ Spanish @ HM @ Other Not Described
1012820000270 @ Male @ Married @ English @ N @ Other Not Described
101315

1088847400270 @ Male @ Married @ English @ U @ White
1088880200270 @ Male @ Married @ English @ HJ @ Black/African Am.
1088886900270 @ Female @ Widower @ English @ N @ White
1088927000270 @ Male @ Widower @ Spanish @ H @ White
1089018400270 @ Male @ Married @ English @ N @ Black/African Am.
1089678200270 @ Female @ Single @ Russian @ N @ White
1089910800270 @ Female @ Married @ Thai @ N @ Asian
1090426900270 @ Female @ Married @ English @ N @ White
1090478300270 @ Male @ Married @ English @ U @ Asian
1092290700270 @ Male @ Married @ Albanian @ N @ White
1092523600270 @ Male @ Married @ English @ D @ White
1092588000270 @ Male @ Married @ English @ U @ Black/African Am.
1093471400270 @ Female @ Divorced @ English @ D @ Declined
1094284500270 @ Female @ Widower @ English @ N @ White
1094892300270 @ Male @ Married @ English @ N @ Other Not Described
1095101500270 @ Male @ Married @ English @ N @ White
1095496900270 @ Male @ Married @ English @ U @ White
1096386900270 @ Female @ Single @ E

1155132700270 @ Male @ M @ ENG @ N @ A
1155343900270 @ Male @ Single @ English @ N @ Black/African Am.
1155430800270 @ Male @ Married @ English @ N @ White
1155870300270 @ Female @ M @ ENG @ N @ W
1156508600270 @ Female @ Single @ Spanish @ H @ Other Not Described
1156614200270 @ Female @ Single @ English @ N @ White
1157337500270 @ Male @ Married @ English @ N @ Declined
1157423500270 @ Male @ Married @ English @ HM @ Other Not Described
1157502700270 @ Female @ M @ SPA @ HM @ O
1157621100270 @ Male @ Married @ English @ N @ Black/African Am.
1157642700270 @ Male @ Married @ English @ N @ White
1157663000270 @ Male @ Married @ English @ H @ White
1157687100270 @ Female @ Single @ English @ N @ White
1157974600270 @ Female @ Single @ English @ H @ Other Not Described
1158988800270 @ Male @ Widower @ English @ N @ White
1159085700270 @ Female @ Widower @ English @ N @ Black/African Am.
1160703100270 @ Male @ Married @ Cantonese @ N @ Asian
1161153600270 @ Male @ Married @ English @ U @ 

1232809200270 @ Male @ Married @ Spanish @ N @ White
1232812500270 @ Female @ Married @ English @ U @ Declined
1232815900270 @ Female @ Single @ English @ N @ Black/African Am.
1232844900270 @ Male @ Married @ English @ N @ Black/African Am.
1232942000270 @ Female @ Widower @ English @ N @ White
1233365500270 @ Male @ Married @ English @ N @ White
1233505500270 @ Male @ Single @ English @ D @ Other Not Described
1233578900270 @ Male @ Married @ English @ N @ Black/African Am.
1233639400270 @ Male @ Married @ English @ N @ White
1233657900270 @ Female @ Married @ English @ U @ White
1234306600270 @ Female @ Single @ English @ N @ Black/African Am.
1234738100270 @ Female @ Widower @ English @ N @ Black/African Am.
1235027000270 @ Female @ Married @ English @ D @ White
1235396900270 @ Male @ Married @ English @ N @ Other Not Described
1235663600270 @ Female @ Married @ English @ N @ White
1235742900270 @ Female @ Single @ English @ N @ White
1235753500270 @ Female @ Single @ English @ H @

In [77]:
user_quartile=pd.read_excel(path + '2_quartile_analysis_eddc_cv3_notcancelled.xlsx', sheet_name='eddc_orderset_order')

In [78]:
Q1=[]
for user in user_quartile[user_quartile['Q1']==1]['userguid']:
    Q1.append(user)
Q3=[]
for user in user_quartile[user_quartile['Q4']==1]['userguid']:
    Q3.append(user)

In [79]:
userguid=[]
for pid in data:
    for date in data[pid]['appt']:
        for u in data[pid]['appt'][date]['user']:
            if u not in userguid:
                userguid.append(u)
print(len(userguid))

3837


get list of unique diagnoses

In [80]:
diaglist = list()
for pid in data:
    if len(data[pid]['appt']) != 0:
        for date in sorted(iter(data[pid]['appt'])):
            if 'withinappt' not in data[pid]['appt'][date] or len(data[pid]['appt'][date]['withinappt']) == 0:
                for i in data[pid]['appt'][date]['diag']:
                    diaglist.append(i)
                    # for key, value in i.items():
                    #     diaglist.append(value)
            elif len(data[pid]['appt'][date]['withinappt']) > 0:
                for time in sorted(iter(data[pid]['appt'][date]['withinappt'])):
                    for i in data[pid]['appt'][date]['withinappt'][time]['diag']:
                        for key, value in i.items():
                            diaglist.append(value)

In [81]:
c_diag=Counter(diaglist)
c_diag.most_common()

[(nan, 6439),
 ('I50.9', 2631),
 ('R06.02', 1285),
 ('N17.9', 812),
 ('I48.91', 752),
 ('I50.23', 652),
 ('I10', 566),
 ('I50.33', 462),
 ('R07.9', 427),
 ('R06.00', 424),
 ('J18.9', 417),
 ('I25.10', 362),
 ('E11.9', 337),
 ('D64.9', 317),
 ('R09.02', 230),
 ('I50.21', 220),
 ('I50.20', 213),
 ('I50.30', 205),
 ('I34.0', 191),
 ('R60.0', 186),
 ('N18.9', 181),
 ('N39.0', 178),
 ('R10.9', 177),
 ('R41.82', 176),
 ('R05', 169),
 ('J44.1', 166),
 ('E87.70', 165),
 ('J44.9', 159),
 ('J96.00', 158),
 ('A41.9', 151),
 ('R79.89', 144),
 ('I50.1', 142),
 ('E78.5', 138),
 ('I95.9', 136),
 ('E87.1', 136),
 ('N18.6', 135),
 ('W19.XXXA', 135),
 ('R50.9', 133),
 ('D72.829', 131),
 ('I21.4', 130),
 ('R57.0', 129),
 ('E87.5', 127),
 ('R53.1', 124),
 ('I47.2', 122),
 ('I50.22', 119),
 ('J90', 119),
 ('M79.89', 118),
 ('J96.01', 117),
 ('I50.43', 116),
 ('K92.2', 114),
 ('R60.9', 107),
 ('R78.81', 106),
 ('Z51.5', 106),
 ('I25.5', 106),
 ('I42.9', 98),
 ('I47.1', 98),
 ('R41.0', 97),
 ('I35.0', 96),
 

In [82]:
diaglist=list(set(diaglist))

In [83]:
#create VTE outcome
import math
c=Counter(diaglist)
num=0
for i in c:
    if isinstance(i, float)==False:
        if i[0:3]=='I82':
            num=num+c[i]
num

19

In [84]:
orderlist = []
for pid in data:
    if len(data[pid]['appt']) != 0:
        for date in sorted(iter(data[pid]['appt'])):
            if 'withinappt' not in data[pid]['appt'][date] or len(data[pid]['appt'][date]['withinappt']) == 0:
                for icd in range(len(data[pid]['appt'][date]['proc'])):
                    orderlist.append(str(data[pid]['appt'][date]['proc'][icd]))
            elif len(data[pid]['appt'][date]['withinappt']) > 0:
                for time in sorted(iter(data[pid]['appt'][date]['withinappt'])):
                    for p in data[pid]['appt'][date]['withinappt'][time]['proc']:
                        orderlist.append(p)

In [85]:
c_order=Counter(orderlist)
c_order.most_common()

[('OSAM Lab Order Set', 40300),
 ('OSCommonly Used Orders - AM Draw', 36790),
 ('Lab_order', 35984),
 ('12 hour order check up to', 31405),
 ('OSMED - ED Admitted Patient Order Set', 5735),
 ('OSCTS AM Labs Order Set', 5363),
 ('General Nursing', 5320),
 ('OSUrine Lab Order Set', 4259),
 ('OSED Order Set - A General Comprehensive Order Set', 3517),
 ('Notify MD/NP/PA', 2547),
 ('IV, Peripheral Access', 2427),
 ('OSHeparin  Drip Order Set (Adult)', 2299),
 ('B/p, hr, rr and temp', 2295),
 ('Nursing Teaching/Counseling', 2260),
 ('VTE Order', 2248),
 ('OSBlood Culture x2', 2196),
 ('OSMED - ED Admitted Patient Order Set (LMH)', 1979),
 ('OSWarfarin Order Set', 1888),
 ('Designated Provider Information', 1741),
 ('OSED Order Set - General (LMH)', 1719),
 ('Admit Patient Order - NYP', 1660),
 ('Exception to NYS Prescription Monitoring Program (PMP) Registry Consultation',
  1656),
 ('I and O, strict', 1548),
 ('Discharge Patient', 1530),
 ('Weight', 1464),
 ('OSED Order Set - A General Com

In [86]:
orderlist=list(set(orderlist))

In [87]:
druglist = []
for pid in data:
    if len(data[pid]['appt']) != 0:
        for date in sorted(iter(data[pid]['appt'])):
            if 'withinappt' not in data[pid]['appt'][date] or len(data[pid]['appt'][date]['withinappt']) == 0:
                for icd in range(len(data[pid]['appt'][date]['drug'])):
                    druglist.append(data[pid]['appt'][date]['drug'][icd])
                    # druglist.append(data[pid]['appt'][date]['drug'][icd]['name'])
            elif len(data[pid]['appt'][date]['withinappt']) > 0:
                for time in sorted(iter(data[pid]['appt'][date]['withinappt'])):
                    for p in data[pid]['appt'][date]['withinappt'][time]['drug']:
                        druglist.append(p['name'])

In [88]:
c_drug=Counter(druglist)
c_drug.most_common()

[('Furosemide Inj', 4875),
 ('Potassium Chloride Oral', 3264),
 ('Magnesium Sulfate Inj', 2850),
 ('Warfarin Sodium Oral', 2691),
 ('Magnesium Oxide Oral', 2576),
 ('Bumetanide Inj', 1726),
 ('Acetaminophen Tab', 1561),
 ('Potassium Chloride Oral Liq', 1272),
 ('Potassium Chloride Inj', 1245),
 ('Dextrose 50% Inj', 1108),
 ('Albuterol Inh Soln', 1022),
 ('Furosemide Oral', 1011),
 ('Influenza Virus Vaccine Inj >3 Years Old', 933),
 ('Pneumococcal 23-Valent Vacc (Pneumovax)', 876),
 ('Senna Oral', 818),
 ('Atorvastatin Tab', 815),
 ('Docusate Sodium Cap', 781),
 ('Ipratropium Bromide Inh Soln', 779),
 ('Normal Saline Bolus', 739),
 ('Glucagon Inj', 721),
 ('Calcium Gluconate Inj', 697),
 ('Heparin Inj', 694),
 ('Glucose Gel Oral', 685),
 ('Aspirin EC Tab', 674),
 ('HYDROmorphone Inj', 668),
 ('Sodium Citrate Inj 4%', 651),
 ('Polyethylene Glycol Oral', 632),
 ('Insulin Aspart Prandial Scale Pre-Meal', 622),
 ('Insulin Aspart Bedtime Scale', 612),
 ('Metolazone Oral', 610),
 ('Vancomycin

In [89]:
druglist=list(set(druglist))

In [90]:
len(diaglist)

1584

In [91]:
len(orderlist)

896

In [92]:
len(druglist)

965

In [ ]:
#generate number of diagnosis
diaglistpt={}
for pid in data:
    diaglistpt[pid]=[]
    for date in data[pid]['appt']:
        for icd in data[pid]['appt'][date]['diag']:
            if icd not in diaglistpt[pid] and pd.isna(icd)==False:
                diaglistpt[pid].append(icd)
    #print(pid,len(diaglistpt[pid]))

In [ ]:
diag_tf={}
for item in diaglist:
    diag_tf[item]={}
    for pid in data:
        diag_tf[item][pid]=0
        for date in data[pid]['appt']:
            for icd in data[pid]['appt'][date]['diag']:
                if icd==item:
                    diag_tf[item][pid]=1/len(diaglistpt[pid])

In [ ]:
diag_df={}
for item in diaglist:
    diag_df[item]=[]
    for pid in data:
        for date in data[pid]['appt']:
            for icd in data[pid]['appt'][date]['diag']:
                if icd==item and pid not in diag_df[item] and pd.isna(icd)==False:
                    diag_df[item].append(pid)

In [ ]:
N=len(data)
diag_idf={}
for item in diaglist:
    diag_idf[item]=np.log(N/(len(diag_df[item])+1)) 

In [ ]:
diag_td_idf={}
for item in diaglist:
    diag_td_idf[item]={}
    for pid in data:
        diag_td_idf[item][pid]=diag_tf[item][pid]*diag_idf[item]

In [ ]:
diag_td_idf_list={}
for item in diag_td_idf:
    diag_td_idf_list[item]=sum(diag_td_idf[item].values())

In [ ]:
{k: v for k, v in sorted(diag_td_idf_list.items(), key=lambda item: item[1], reverse=True)}

td_idf for orders

In [ ]:
#generate number of orders
orderlistpt={}
for pid in data:
    orderlistpt[pid]=[]
    for date in data[pid]['appt']:
        for icd in data[pid]['appt'][date]['proc']:
            if pd.isna(icd)==False:
                orderlistpt[pid].append(icd)
    #print(pid,len(diaglistpt[pid]))

In [ ]:
order_tf={}
for item in orderlist:
    order_tf[item]={}
    for pid in data:
        order_tf[item][pid]=0
        for date in data[pid]['appt']:
            for icd in data[pid]['appt'][date]['proc']:
                if icd==item and pd.isna(icd)==False:
                    order_tf[item][pid]=(order_tf[item][pid]+1)/len(orderlistpt[pid])

In [ ]:
order_df={}
for item in orderlist:
    order_df[item]=[]
    for pid in data:
        for date in data[pid]['appt']:
            for icd in data[pid]['appt'][date]['proc']:
                if icd==item and pid not in order_df[item] and pd.isna(icd)==False:
                    order_df[item].append(pid)

In [ ]:
N=len(data)
order_idf={}
for item in orderlist:
    order_idf[item]=np.log(N/(len(order_df[item])+1)) 

In [ ]:
order_td_idf={}
for item in orderlist:
    order_td_idf[item]={}
    for pid in data:
        order_td_idf[item][pid]=order_tf[item][pid]*order_idf[item]

In [ ]:
order_td_idf_list={}
for item in order_td_idf:
    order_td_idf_list[item]=sum(order_td_idf[item].values())

In [ ]:
{k: v for k, v in sorted(order_td_idf_list.items(), key=lambda item: item[1], reverse=True)}

td_idf for drugs

In [105]:
cluster

clientvisitguid  cluster_pull2  cluster_notcancelled  \
0     9000556943700270              1                     1   
1     9000562000000270              1                     1   
2     9000567313100270              2                     1   
3     9000582002300270              3                     1   
4     9000584744300270              1                     2   
5     9000608150700270              1                     4   
6     9000624731800270              1                     1   
7     9000624817200270              1                     2   
8     9000653284000270              1                     2   
9     9000684111000270              1                     3   
10    9000685526500270              1                     3   
11    9000737643900270              3                     3   
12    9000763338100270              3                     2   
13    9000763976700270              1                     1   
14    9000766032300270              1                     1   
15    9000768628200270              2                     3   
16    9000771224000270              2                     2   
17    9000774599200270              2                     1   
18    9000778172900270              1                     1   
19    9000778912000270              1                     2   
20    9000781162000270              1                     2   
21    9000786831400270              3                     2   
22    9000787961400270              3                     3   
23    9000789394000270              1                     1   
24    9000789853200270              1                     1   
25    9000790112500270              1                     1   
26    9000790635800270              1                     2   
27    9000791127000270              1                     1   
28    9000791130400270              1                     1   
29    9000791560800270              3                     2   
...                ...            ...                   ...   
1382  9001268682700270              1                     1   
1383  9001269084300270              3                     2   
1384  9001270810600270              1                     1   
1385  9001271511400270              1                     3   
1386  9001271703900270              3                     2   
1387  9001271734400270              1                     4   
1388  9001271803700270              1                     2   
1389  9001272344700270              1                     3   
1390  9001272408600270              1                     3   
1391  9001273735100270              1                     2   
1392  9001273899200270              1                     1   
1393  9001274504100270              1                     2   
1394  9001274664700270              3                     2   
1395  9001275185300270              1                     2   
1396  9001275904000270              1                     1   
1397  9001276744100270              1                     1   
1398  9001277843700270              1                     1   
1399  9001279481500270              1                     3   
1400  9001279949200270              1                     2   
1401  9001281548600270              1                     1   
1402  9001282574700270              1                     1   
1403  9001282870100270              1                     2   
1404  9001282891400270              1                     1   
1405  9001282931300270              1                     1   
1406  9001283296000270              1                     1   
1407  9001283883400270              1                     1   
1408  9001284311200270              1                     1   
1409  9001284903800270              1                     1   
1410  9001284909400270              1                     1   
1411  9001285016600270              1                     1   

      cluster_notcancelld_4  OSpercent  age  LOS  30day  60day  90ay  ...  \
0                      

In [166]:
data_C1=deepcopy(data)

In [167]:
for pid in data:
    if len(cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values)>1:
        if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==1:
            pass
        else:
            del data_C1[pid]
                
    else:
        del data_C1[pid]

In [168]:
len(data_C1)

0

In [113]:
druglistpt={}
for pid in data:
  if len(cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values)>1:
      if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==1:
        druglistpt[pid]=[]
        for date in data[pid]['appt']:
            for icd in data[pid]['appt'][date]['drug']:
                if pd.isna(icd)==False:
                    druglistpt[pid].append(icd)
        #print(pid,len(diaglistpt[pid]))

In [114]:
drug_tf={}
for item in druglist:
    drug_tf[item]={}
    for pid in data:
      if len(cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values)>1:
          if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==1:
            drug_tf[item][pid]=0
            for date in data[pid]['appt']:
                for icd in data[pid]['appt'][date]['drug']:
                    if icd==item and pd.isna(icd)==False:
                        drug_tf[item][pid]=(drug_tf[item][pid]+1)/len(druglistpt[pid])

KeyboardInterrupt: 

In [ ]:
drug_df={}
for item in druglist:
    drug_df[item]=[]
    for pid in data:
      if len(cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values)>1:
          if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==1:
            print('f')
            for date in data[pid]['appt']:
                for icd in data[pid]['appt'][date]['drug']:
                    if icd==item and pid not in drug_df[item] and pd.isna(icd)==False:
                        drug_df[item].append(pid)

In [ ]:
N=len(data)
drug_idf={}
for item in druglist:
    drug_idf[item]=np.log(N/(len(drug_df[item])+1))

In [ ]:
drug_td_idf={}
for item in druglist:
    drug_td_idf[item]={}
    for pid in data:
        drug_td_idf[item][pid]=drug_tf[item][pid]*drug_idf[item]

In [ ]:
drug_td_idf_list={}
for item in drug_td_idf:
    drug_td_idf_list[item]=sum(drug_td_idf[item].values())

In [ ]:
{k: v for k, v in sorted(drug_td_idf_list.items(), key=lambda item: item[1], reverse=True)}

skip for now

In [ ]:
import matplotlib.pylab as plt

lists = sorted(drug_td_idf_list.items(), key=lambda item: item[1],reverse=True)
x, y = zip(*lists) # unpack a list of pairs into two tuples
numBins = 10
plt.hist(y,numBins, density=True, cumulative=1)
plt.show()

In [ ]:
import matplotlib.pylab as plt

lists = sorted(order_td_idf_list.items(), key=lambda item: item[1])
x, y = zip(*lists) # unpack a list of pairs into two tuples
numBins = 10
plt.hist(y,numBins, density=True, cumulative=True)
plt.show()

In [ ]:
drug_td_idf_df=pd.DataFrame.from_dict(drug_td_idf, orient='index')
drug_td_idf_df=drug_td_idf_df.T

In [ ]:
order_td_idf_df=pd.DataFrame.from_dict(order_td_idf, orient='index')
order_td_idf_df=order_td_idf_df.T

In [ ]:
result = pd.concat([order_td_idf_df, drug_td_idf_df], axis=1, join='inner')

In [ ]:
from sklearn import cluster
from sklearn.cluster import MiniBatchKMeans
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
mat = result.values
# Using sklearn
km = cluster.KMeans(n_clusters=6,random_state=3425)
km.fit(mat)
# Get cluster assignment labels
labels = km.labels_
# Format results as a DataFrame
results = pd.DataFrame([result.index,labels]).T

In [ ]:
from sklearn import cluster
from sklearn.cluster import MiniBatchKMeans
#clusters=MiniBatchKMeans(n_clusters=6, random_state=20).fit(result)
clusters=cluster.KMeans(n_clusters=14, random_state=20).fit(result)
labels = clusters.labels_
results = pd.DataFrame([result.index,labels]).T
results.groupby([1]).count()

In [ ]:
from sklearn.cluster import MiniBatchKMeans
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
def find_optimal_clusters(data, max_k):
    iters = range(2, max_k+1, 2)
    
    sse = []
    for k in iters:
        #sse.append(MiniBatchKMeans(n_clusters=k, init_size=1024, batch_size=2048,random_state=20).fit(data).inertia_)
        sse.append(cluster.KMeans(n_clusters=k, random_state=20).fit(data).inertia_)
        
        print('Fit {} clusters'.format(k))
        
    f, ax = plt.subplots(1, 1)
    ax.plot(iters, sse, marker='o')
    ax.set_xlabel('Cluster Centers')
    ax.set_xticks(iters)
    ax.set_xticklabels(iters)
    ax.set_ylabel('SSE')
    ax.set_title('SSE by Cluster Center Plot')
    
find_optimal_clusters(result, 40)

In [ ]:
clusters = MiniBatchKMeans(n_clusters=14, init_size=1024, batch_size=2048, random_state=20).fit_predict(result)

In [ ]:
results.to_csv(path+"tfidf_kmeans10.csv", index=False)

get diagnoses, orders, and drugs observed by 90%+ of the patients

In [93]:
N=len(data)

In [94]:
N

1651

In [96]:
diagNotusedbyall=[]
used={}
for item in diaglist:
    used[item]={}  
    for pid in data:
        stop=False
        used[item][pid]=0
        for date in data[pid]['appt']:
            for i in data[pid]['appt'][date]['diag']:
                if i==item:
                    used[item][pid]=1
                    stop=True
                    break
            if stop==True:
                break
    if sum(used[item].values())>N*0.3 : #used by more than 30% of patients
        diagNotusedbyall.append(item)       

In [97]:
diagNotusedbyall

['N17.9', 'I50.9', 'R06.02']

In [98]:
orderNotusedbyall=[]
used={}
for item in orderlist:
    used[item]={}  
    for pid in data:
        stop=False
        used[item][pid]=0
        for date in data[pid]['appt']:
            for i in data[pid]['appt'][date]['proc']:
                if i==item:
                    used[item][pid]=1
                    stop=True
                    break
            if stop==True:
                break
    if sum(used[item].values())>N*0.8 : #used by more than 80% of patients
        orderNotusedbyall.append(item)           

In [99]:
len(c_order)

896

In [100]:
commonorder=[]
for i in c_order.most_common(10):
    commonorder.append(i[0])
commonorder

['OSAM Lab Order Set',
 'OSCommonly Used Orders - AM Draw',
 'Lab_order',
 '12 hour order check up to',
 'OSMED - ED Admitted Patient Order Set',
 'OSCTS AM Labs Order Set',
 'General Nursing',
 'OSUrine Lab Order Set',
 'OSED Order Set - A General Comprehensive Order Set',
 'Notify MD/NP/PA']

In [101]:
commondrug=[]
for i in c_drug.most_common(10):
    commondrug.append(i[0])
commondrug

['Furosemide Inj',
 'Potassium Chloride Oral',
 'Magnesium Sulfate Inj',
 'Warfarin Sodium Oral',
 'Magnesium Oxide Oral',
 'Bumetanide Inj',
 'Acetaminophen Tab',
 'Potassium Chloride Oral Liq',
 'Potassium Chloride Inj',
 'Dextrose 50% Inj']

In [102]:
drugNotusedbyall=[]
used={}
for item in druglist:
    used[item]={}  
    for pid in data:
        stop=False
        used[item][pid]=0
        for date in data[pid]['appt']:
            for i in data[pid]['appt'][date]['drug']:
                if i==item:
                    used[item][pid]=1
                    stop=True
                    break
            if stop==True:
                break
    if sum(used[item].values())>N*0.5 : #used by more than 50% of patients
        drugNotusedbyall.append(item)     

In [103]:
drugNotusedbyall #used by more than 50% of patients

['Pneumococcal 23-Valent Vacc (Pneumovax)',
 'Acetaminophen Tab',
 'Influenza Virus Vaccine Inj >3 Years Old',
 'Furosemide Inj']

In [ ]:
# drugNotusedbyall=[]
# for item in druglist:
#     used=0
#     for pid in data:
#         for date in data[pid]['appt']:
#             for i in data[pid]['appt'][date]['drug']:
#                 if i==item:
#                     used+=1
    
#     if used>500 :
#         drugNotusedbyall.append(item)       

In [104]:
for pid in data:
    for date in sorted(iter(data[pid]['appt'])):
        data[pid]['appt'][date]['type'] = 'I'

In [105]:
data2 = deepcopy(data)

In [106]:
len(data2)

1651

re-labeling orders

In [107]:
for pid in data:
    for date in sorted(data[pid]['appt']):
        data2[pid]['appt'][date]['diag'] = []
        data2[pid]['appt'][date]['proc'] = []
        data2[pid]['appt'][date]['drugclass'] = []
        data2[pid]['appt'][date]['drug'] = []
        data2[pid]['appt'][date]['user']=[]
#         for icd in range(len(data[pid]['appt'][date]['diag'])):
#             if data[pid]['appt'][date]['diag'][icd] in diagNotusedbyall and data[pid]['appt'][date]['diag'][icd] not in data2[pid]['appt'][date]['diag']: #ADD ONLY DIAGNOSIS THAT WE WANT
#                 data2[pid]['appt'][date]['diag'].append(data[pid]['appt'][date]['diag'][icd])

        for icd in range(len(data[pid]['appt'][date]['proc'])):
            if data[pid]['appt'][date]['proc'][icd] in commonorder and data[pid]['appt'][date]['proc'][icd] not in data2[pid]['appt'][date]['proc']:
                if data[pid]['appt'][date]['proc'][icd]=='OSAM Lab Order Set' or data[pid]['appt'][date]['proc'][icd]=='OSCTS AM Labs Order Set':
                    data2[pid]['appt'][date]['proc'].append('OSCommonly Used Orders - AM Draw')
                elif data[pid]['appt'][date]['proc'][icd]=='Lab_order':
                    pass
                elif data[pid]['appt'][date]['proc'][icd][0:2]=='OS':
                    data2[pid]['appt'][date]['proc'].append(str(data[pid]['appt'][date]['proc'][icd]))
                else:
#                     data2[pid]['appt'][date]['proc'].append(str(data[pid]['appt'][date]['proc'][icd]))
                    pass
                data2[pid]['appt'][date]['proc']=list(set(data2[pid]['appt'][date]['proc']))
#             if data[pid]['appt'][date]['proc'][icd]== 'Clinical Pathway - Heart Failure Order Set':
#                 data2[pid]['appt'][date]['proc'].append(str(data[pid]['appt'][date]['proc'][icd]))
#             if data[pid]['appt'][date]['proc'][icd]==  'Clinical Pathway - Heart Failure Order Set (LMH)':
#                 data2[pid]['appt'][date]['proc'].append('Clinical Pathway - Heart Failure Order Set')
                
#             if data[pid]['appt'][date]['proc'][icd]==  'ED Order set - Dyspnea/CHF/COPD/Asthma':
#                 data2[pid]['appt'][date]['proc'].append(str(data[pid]['appt'][date]['proc'][icd]))
#             if data[pid]['appt'][date]['proc'][icd]==   'ED Order set - Dyspnea/CHF/COPD/Asthma (LMH)':
#                 data2[pid]['appt'][date]['proc'].append('ED Order set - Dyspnea/CHF/COPD/Asthma')

        for icd in range(len(data[pid]['appt'][date]['drug'])):
            if data[pid]['appt'][date]['drug'][icd] in drugNotusedbyall and data[pid]['appt'][date]['drug'][icd] not in data2[pid]['appt'][date]['drugclass']:
                if str(data[pid]['appt'][date]['drug'][icd])== 'Furosemide Inj' or str(data[pid]['appt'][date]['drug'][icd])== 'Furosemide Oral':
                    data2[pid]['appt'][date]['drugclass'].append('Furosemide')
                    
                elif str(data[pid]['appt'][date]['drug'][icd])==  'Insulin Aspart Prandial Scale Pre-Meal' or str(data[pid]['appt'][date]['drug'][icd])==  'Insulin Aspart Bedtime Scale':
                    data2[pid]['appt'][date]['drugclass'].append('Insulin Aspart')
                elif str(data[pid]['appt'][date]['drug'][icd])==  'Potassium Chloride Inj' or str(data[pid]['appt'][date]['drug'][icd])== 'Potassium Chloride Oral' or str(data[pid]['appt'][date]['drug'][icd])==  'Potassium Chloride Oral Liq':
                    data2[pid]['appt'][date]['drugclass'].append('Potassium Chloride') 
                else:
                    data2[pid]['appt'][date]['drugclass'].append(data[pid]['appt'][date]['drug'][icd])
                    
                data2[pid]['appt'][date]['drugclass']=list(set(data2[pid]['appt'][date]['drugclass']))

        for u in data[pid]['appt'][date]['user']:
            if u in Q1 and 'Q1' not in data2[pid]['appt'][date]['user']:
                data2[pid]['appt'][date]['user'].append('Q1')
            if u in Q3 and 'Q3' not in data2[pid]['appt'][date]['user']:
                data2[pid]['appt'][date]['user'].append('Q3')

In [108]:
for pid in data2:
    for date in data2[pid]['appt']:
        print(data2[pid]['appt'][date]['drugclass'])

[]
[]
[]
[]
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)']
[]
[]
[]
['Acetaminophen Tab']
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)', 'Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)']
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)']
[]
[]
['Furosemide']
[]
[]
[]
['Furosemide']
[]
['Furosemide']
[]
[]
[]
['Furosemide']
[]
[]
['Acetaminophen Tab']
[]
[]
['F

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
['Furosemide']
[]
[]
[]
['Acetaminophen Tab']
[]
['Furosemide']
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]


['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)', 'Furosemide', 'Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)',

[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Pneumococcal 23-Valent Vacc (Pneumovax)', 'Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab', 'Pneumococcal 23-Valent Vacc (Pneumovax)', 'Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
['Furosemide']
[]
['Acetaminophen Tab']
[]
[]
['Furosemide']
[]
['Furosemide']
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
['Fu

...

[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Furosemide']
[]
[]
[]
[]
['Furosemide']
[

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
['Acetaminophen Tab']
['Furosemide']
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Furosemide']
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
['Acetaminophen Tab']
['Acetaminophen Tab', 'Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Acetaminophen Tab']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
['Acetaminophen Tab', 'Influenza Virus Vaccine Inj >3 Years Old', 'Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
['Furosemide']
[]
[]
['Acetaminophen Tab']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
['Influenza Virus Vaccine Inj >3 Years Old'

['Furosemide']
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Influenza Virus Vaccine Inj >3 Years Old', 'Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
['Influenza Virus Vaccine Inj >3 Years Old']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Ac

[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
['Influenza Virus Vaccine Inj >3 Years Old']
[]
['Furosemide']
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
['Influenza Virus Vaccine Inj >3 Years Old']
['Acetaminophen Tab']
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
['Furosemide']
['Furosemide']
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Furosemide']
[]
[]
['Furosemide']
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
['Acetaminophen Tab']
[]
[]
[]
[]
[]
[]
[]


In [109]:
pidcount=[]
for pid in data2:
    for date in data2[pid]['appt']:
        if len(data2[pid]['appt'][date]['drugclass'])>0 or len(data2[pid]['appt'][date]['proc'])>0:
            pidcount.append(pid)
            
#             print(data2[pid]['appt'][date]['drugclass'],data2[pid]['appt'][date]['proc'])
pidcount=list(set(pidcount))
print(len(pidcount))

1650


In [110]:
len(data2)

1651

In [111]:
JSON_FILE = os.path.expanduser(path+"2_EDDC_HF_data_filtered_OS_cv3_notcancelled.json")

with open(JSON_FILE, 'w') as outfile:
    json.dump(data2, outfile, indent=2, sort_keys=True, separators=(',', ': '))


In [112]:
pickle_out = open(path + '2_EDDC_HF_data_filtered_OS_cv3_notcancelled.pickle', 'wb')
pickle.dump(data2, pickle_out)
pickle_out.close()

#get number of users for patients who appeared in data2, if patient is seen by >1 user, remove. Else, categorize patient as treated by high/low users

In [113]:
piduser={}
for pid in data2:
    piduser[pid]=[]
    for date in data2[pid]['appt']:
        for i in data2[pid]['appt'][date]['user']:
            piduser[pid].append(i)
    if len(piduser[pid])>0:
        piduser[pid]=list(set(piduser[pid]))

In [114]:
piduser

{'556943700270': ['Q3', 'Q1'],
 '561002000270': ['Q3', 'Q1'],
 '562000000270': ['Q3', 'Q1'],
 '567313100270': ['Q3', 'Q1'],
 '579333200270': ['Q3', 'Q1'],
 '582002300270': ['Q1'],
 '584744300270': ['Q3', 'Q1'],
 '608150700270': ['Q3', 'Q1'],
 '624731800270': ['Q3', 'Q1'],
 '624817200270': ['Q3', 'Q1'],
 '653284000270': ['Q3', 'Q1'],
 '684111000270': ['Q3', 'Q1'],
 '685155700270': ['Q3', 'Q1'],
 '685526500270': ['Q1'],
 '737643900270': ['Q3', 'Q1'],
 '763338100270': ['Q3', 'Q1'],
 '763976700270': ['Q1'],
 '766032300270': ['Q3', 'Q1'],
 '768628200270': ['Q3', 'Q1'],
 '771224000270': ['Q3', 'Q1'],
 '774599200270': ['Q1'],
 '778172900270': ['Q3', 'Q1'],
 '778912000270': ['Q3', 'Q1'],
 '781162000270': ['Q3', 'Q1'],
 '786831400270': ['Q3', 'Q1'],
 '787961400270': ['Q3', 'Q1'],
 '789394000270': ['Q1'],
 '789853200270': ['Q3', 'Q1'],
 '790112500270': ['Q3', 'Q1'],
 '790635800270': ['Q1'],
 '790857300270': ['Q3', 'Q1'],
 '791127000270': ['Q3'],
 '791130400270': ['Q1'],
 '791560800270': ['Q3', '

In [115]:
piduser2=deepcopy(piduser)
for pid in piduser:
    if len(piduser[pid])==1:
        pass
    else:
        del piduser2[pid]
print(len(piduser2))

650


In [116]:
for pid in piduser2:
    print (pid,piduser2[pid][0])

582002300270 Q1
685526500270 Q1
763976700270 Q1
774599200270 Q1
789394000270 Q1
790635800270 Q1
791127000270 Q3
791130400270 Q1
793140600270 Q1
793451300270 Q1
793475600270 Q1
795395900270 Q1
796870000270 Q3
797148000270 Q1
797214500270 Q3
797484600270 Q1
798001600270 Q3
799591100270 Q3
799604300270 Q1
800566900270 Q1
802639200270 Q1
802707700270 Q1
805374100270 Q1
806399800270 Q3
806478600270 Q1
806970700270 Q3
808073300270 Q1
808093400270 Q1
810004400270 Q1
810691100270 Q3
810727300270 Q1
810813400270 Q1
811449800270 Q3
811451200270 Q3
811457500270 Q1
811459800270 Q1
811476200270 Q1
812526300270 Q3
813528800270 Q3
815333300270 Q1
815441500270 Q1
815909100270 Q1
816933700270 Q1
817506800270 Q1
818265700270 Q3
822184400270 Q1
822570100270 Q1
823415900270 Q1
825655600270 Q1
826526100270 Q3
826527800270 Q3
827067100270 Q1
830270900270 Q1
831699300270 Q1
832820000270 Q3
833258400270 Q1
833289200270 Q1
833302600270 Q3
833616200270 Q1
835085600270 Q1
835270600270 Q3
836107700270 Q1
83662230

In [178]:
data_1Q = deepcopy(data2)
for pid in data2:
    if pid in piduser2:
        if piduser2[pid]==['Q1']:
            pass
        else:
            del data_1Q[pid]
    else:
        del data_1Q[pid]

In [179]:
data_3Q = deepcopy(data2)
for pid in data2:
    if pid in piduser2:
        if piduser2[pid]==['Q3']:
            pass
        else:
            del data_3Q[pid]
    else:
        del data_3Q[pid]

In [180]:
print(len(data_1Q),len(data_3Q))

254 330


In [94]:
#only have HF as diagnosis, got from getSourceData.ipynb
HFlist=[9001251915900270,9001216906000270,9001121093200270,9001173168800270,9001211775200270,9001246400900270,9001220441100270,9001174426900270,9001247254900270,9001109270200270,9001176608700270,9001241780400270,9001234306600270,9001206891600270,9001179229100270,9001265609400270,9001148298400270,9001282931300270,9001246979700270,9001236154600270,9001232695300270,9001283883400270,9001225771000270,9001180467800270,9001235742900270,9001140573400270,9001262036300270,9001277843700270,9001191425900270,9001170806400270,9001143998000270,9001115258800270,9001251701600270,9001189761100270,9001172050300270,9001213409300270,9001174120900270,9001269084300270,9001192844000270,9001187189200270,9001127051300270,9001145898800270,9001241929400270,9001157423500270,9001281548600270,9001277336200270,9001153999000270,9001124832900270,9001103203000270,9001197850700270,9001122106400270,9001183064500270,9001229215400270,9001190326000270,9001283307400270,9001247873000270,9001271734400270,9001137168300270,9001176846300270,9001219793500270,9001205152300270,9001224174300270,9001180232100270,9001162665900270,9001280700600270,9001122902200270,9001283296000270,9001231182100270,9001175917800270,9001118690900270,9001198997800270,9001199107500270,9001257904300270,9001241691500270,9001217549800270,9001133189700270,9001130637700270,9001139094600270,9001134950300270,9001135748000270,9001208316600270,9001139543800270,9001164070700270,9001250210700270,9001161881700270,9001183117300270,9001169276400270,9001188841900270,9001170830800270,9001175772200270,9001175857400270,9001239669600270,9001173008500270,9001176464400270,9001179229900270,9001134997500270,9001213095600270,9001212260100270,9001190777500270,9001261274500270,9001192647900270,9001221808200270,9001204705400270,9001212284600270,9001213056600270,9001226275500270,9001236382900270,9001238991200270,9001234738100270,9001240443800270,9001282946900270,9001260567600270,9001171950100270,9001185043000270,9001256154500270,9001272344700270,9001217202600270,9001273899200270,9001209675100270,9001231430000270,9001124571900270,9001161193900270,9001284903800270,9001144030000270,9001127460400270,9001284311200270,9001142706400270,9001152684100270,9001146841500270]

In [95]:
HFlist=[str(i) for i in HFlist]

In [96]:
s=0
l=0
for pid in data2:
#     if int(pid) in HFlist:
        s=s+data2[pid]['90day_readmit']
        l=l+data2[pid]['LOS']
print(s,l/len(data2))

121 10.642035130224107


compare readmission outcome and LOS across patients treated by high/low users

In [97]:
s=0
l=0
for pid in data_1Q:
#     if int(pid) in HFlist:
        s=s+data_1Q[pid]['90day_readmit']
        l=l+data_1Q[pid]['LOS']
print(s,l/len(data_1Q))

42 9.007920792079208


In [98]:
s=0
l=0
for pid in data_3Q:
#     if int(pid) in HFlist:
        s=s+data_3Q[pid]['90day_readmit']
        l=l+data_3Q[pid]['LOS']
print(s,l/len(data_3Q))

9 5.0271739130434785


In [99]:
#all orders for EDDC_18_89, for Disco
with open(path+'orders_EDDC_18_89_2012_2018.csv', 'w') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    combined_row = []
    combined_row.append('pid')
    combined_row.append('date')
    combined_row.append('activity')
    combined_row.append('user')
    writer.writerow(combined_row)
    for pid in data2:
#         if int(pid) in HFlist:
                for date in data2[pid]['appt']:
                    if len(data2[pid]['appt'][date]['proc'])>0 or len(data2[pid]['appt'][date]['drug'])>0:
                        combined_row = []
                        combined_row.append(pid)
                        #combined_row.append('@')
                        combined_row.append(date)
                        #combined_row.append('@')
                        combined_row.append(str(sorted(data2[pid]['appt'][date]['proc']))+str(sorted(data2[pid]['appt'][date]['drug'])))
                        combined_row.append(data2[pid]['appt'][date]['user'])
                        writer.writerow(combined_row)

In [100]:
#only patients treated by low users, for Disco, change Q1 to Q3 for high users
with open('Q1_orders_EDDC_HFonly_18_89.csv', 'w') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    combined_row = []
    combined_row.append('pid')
    combined_row.append('date')
    combined_row.append('activity')
    combined_row.append('user')
    writer.writerow(combined_row)
    for pid in data2:
        if int(pid) in HFlist and pid in piduser2:
            if piduser2[pid]==['Q1']:
                for date in data2[pid]['appt']:
                    if len(data2[pid]['appt'][date]['proc'])>0 or len(data2[pid]['appt'][date]['drug'])>0:
                        combined_row = []
                        combined_row.append(pid)
                        #combined_row.append('@')
                        combined_row.append(date)
                        #combined_row.append('@')
                        combined_row.append(str(sorted(data2[pid]['appt'][date]['proc']))+str(sorted(data2[pid]['appt'][date]['drug'])))
                        combined_row.append(data2[pid]['appt'][date]['user'])
                        writer.writerow(combined_row)
                

In [101]:
#SPADE on all orders for EDDC_18_89
with open(path+'SPADE_orders_EDDC_HFonly_18_89.csv', 'w') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    writer.writerow(combined_row)
    for pid in data2:
        if int(pid) in HFlist:
            n=0
            for date in data2[pid]['appt']:
                if len(data2[pid]['appt'][date]['proc'])>0 or len(data2[pid]['appt'][date]['drug'])>0:
                    n=n+1
                    combined_row = []
                    combined_row.append(pid)
                    #combined_row.append('@')
                    combined_row.append(n)
                    #combined_row.append('@')
                    combined_row.append('1')
                    combined_row.append(str(sorted(data2[pid]['appt'][date]['proc']))+str(sorted(data2[pid]['appt'][date]['drug'])))
                    writer.writerow(combined_row)

In [102]:
#optional, subgroup for patients with HF diagnosis only
data_18_89_HFonly_EDDC = deepcopy(data2)
for pid in data2:
    if int(pid) in HFlist:
        pass
    else:
        del data_18_89_HFonly_EDDC[pid]

In [103]:
len(data_18_89_HFonly_EDDC)

0

In [104]:
pickle_out = open(path + 'data_18_89_EDDC_2012_2018.pickle', 'wb')
pickle.dump(data, pickle_out)
pickle_out.close()

In [105]:
for pid in data2:
    print(pid,data2[pid]['30day_readmit'],data2[pid]['60day_readmit'],data2[pid]['90day_readmit'],data2[pid]['LOS'],data2[pid]['dischargedisposition'])

556943700270 0 0 0 8 ROUTINE/HOME
561002000270 0 0 0 5 PATIENT EXPIRED
562000000270 0 0 0 9 ROUTINE/HOME
567313100270 0 0 0 52 DISCHARGE TO SNF
579333200270 0 0 0 21 DISCHARGE HOME WITH HM HLTH SERV
582002300270 0 0 0 13 DISCHARGE HOME WITH HM HLTH SERV
584744300270 0 0 0 3 DISCHARGE TO SNF
608150700270 0 0 0 13 DISCHARGE TO LONG TERM CARE
624731800270 0 0 0 16 DISCHARGE TO OTHER FAC NOT LISTED
624817200270 0 0 0 21 ROUTINE/HOME
653284000270 0 0 0 7 TRANS/DISCHARGE TO/FM IP REHAB FAC
684111000270 0 0 0 11 PATIENT EXPIRED
685155700270 0 0 0 26 PATIENT EXPIRED
685526500270 0 0 0 10 ROUTINE/HOME
737643900270 0 0 0 36 PATIENT EXPIRED
763338100270 0 0 0 27 PATIENT EXPIRED
763976700270 0 0 0 7 DISCHARGE TO SNF
766032300270 0 0 0 4 ROUTINE/HOME
768628200270 0 0 0 68 DISCHARGE HOME WITH HM HLTH SERV
771224000270 0 0 0 67 DISCHARGE TO SNF
774599200270 0 0 0 24 DISCHARGE HOME WITH HOSPICE
778172900270 0 0 0 1 DISCHARGE HOME WITH HM HLTH SERV
778912000270 0 0 0 8 ROUTINE/HOME
781162000270 0 0 0 2

865469300270 0 0 0 19 DISCHARGE HOME WITH HM HLTH SERV
865510000270 0 1 1 2 DISCHARGE HOME WITH HM HLTH SERV
866199600270 0 0 0 6 ROUTINE/HOME
866209100270 0 0 0 2 ROUTINE/HOME
866253300270 0 0 0 10 DISCHARGE TO SNF
866582700270 0 0 0 2 ROUTINE/HOME
866772900270 0 0 0 1 DISCHARGE TO SNF
866857900270 0 0 0 7 ROUTINE/HOME
867202400270 0 0 0 3 ROUTINE/HOME
867227800270 0 0 0 27 PATIENT EXPIRED
868298100270 0 0 1 8 DISCHARGE TO SNF
868376200270 0 0 0 3 ROUTINE/HOME
868887700270 0 0 0 3 DISCHARGE HOME WITH HM HLTH SERV
869354800270 0 0 0 13 DISCHARGE HOME WITH HM HLTH SERV
869464500270 0 0 0 6 ROUTINE/HOME
869540500270 0 0 0 3 DISCHARGE TO SNF
869685800270 0 0 0 5 DISCHARGE HOME WITH HM HLTH SERV
869726500270 0 1 1 19 PATIENT EXPIRED
870917200270 0 0 0 61 DISCHARGE TO SNF
870933400270 0 0 0 8 ROUTINE/HOME
870968500270 1 1 1 7 ROUTINE/HOME
871091600270 0 0 0 15 DISCHARGE HOME WITH HM HLTH SERV
871394600270 0 0 0 15 DISCHARGE TO SNF
871658000270 0 0 0 3 DISCHARGE HOME WITH HM HLTH SERV
871726

940945200270 0 0 0 20 DISCHARGE TO SNF
941101900270 0 0 0 4 DISCHARGE TO SNF
941338300270 0 0 0 21 DISCHARGE TO SNF
941467200270 0 0 0 6 AGAINST MEDICAL ADVICE
941601700270 0 0 0 9 DISCHARGE HOME WITH HOSPICE
942192000270 0 0 0 35 DISCHARGE HOME WITH HM HLTH SERV
942450800270 0 0 0 5 ROUTINE/HOME
942474900270 0 0 0 7 DISCHARGE TO SNF
942720300270 0 0 0 4 DISCHARGE TO SNF
943496200270 0 0 0 13 ROUTINE/HOME
944007900270 0 0 0 26 DISCHARGE HOME WITH HM HLTH SERV
944551800270 0 0 0 6 DISCHARGE HOME WITH HM HLTH SERV
945047700270 0 0 0 12 DISCHARGE TO SNF
945445100270 0 0 0 10 DISCHARGE HOME WITH HM HLTH SERV
945472500270 0 0 0 20 DISCHARGE HOME WITH HM HLTH SERV
945546900270 0 0 0 9 DISCHARGE TO SNF
945549800270 0 0 0 2 ROUTINE/HOME
945847800270 0 0 0 4 DISCHARGE TO SNF
946014400270 0 0 0 6 DISCHARGE HOME WITH HM HLTH SERV
947133000270 1 1 1 8 DISCHARGE HOME WITH HM HLTH SERV
947233000270 0 0 0 5 ROUTINE/HOME
947322400270 0 0 0 5 PATIENT EXPIRED
947728500270 1 1 1 4 DISCHARGE TO SNF
947796

1011151100270 0 0 0 9 DISCHARGE TO ACUTE FACILITY
1011331400270 0 0 0 3 DISCHARGE HOME WITH HM HLTH SERV
1011739000270 0 0 0 3 ROUTINE/HOME
1011810500270 0 0 0 9 PATIENT EXPIRED
1012091300270 0 0 0 0 ROUTINE/HOME
1012820000270 0 0 0 106 DISCHARGE HOME WITH HM HLTH SERV
1013154400270 0 0 0 1 DISCHARGE HOME WITH HM HLTH SERV
1013255800270 0 0 0 6 DISCHARGE HOME WITH HM HLTH SERV
1013341500270 0 0 0 1 ROUTINE/HOME
1013345800270 0 0 0 5 ROUTINE/HOME
1014393100270 0 0 0 7 DISCHARGE HOME WITH HM HLTH SERV
1014970200270 0 0 0 8 ROUTINE/HOME
1015858600270 0 0 0 12 DISCHARGE HOME WITH HM HLTH SERV
1016068400270 0 0 0 3 ROUTINE/HOME
1016448800270 0 0 0 4 ROUTINE/HOME
1016551300270 0 0 0 3 DISCHARGE HOME WITH HM HLTH SERV
1017218600270 0 1 1 1 ROUTINE/HOME
1017710500270 0 0 0 1 DISCHARGE HOME WITH HM HLTH SERV
1018849100270 0 0 0 43 DISCHARGE TO SNF
1019198400270 0 0 0 5 DISCHARGE HOME WITH HM HLTH SERV
1019985700270 0 0 0 7 DISCHARGE TO SNF
1020060200270 0 0 0 2 DISCHARGE HOME WITH HM HLTH SERV


1087614900270 0 0 0 4 DISCHARGE HOME WITH HM HLTH SERV
1087662400270 0 0 0 7 ROUTINE/HOME
1088094700270 0 0 0 3 ROUTINE/HOME
1088769500270 0 0 0 31 DISCHARGE TO SNF
1088770700270 0 0 0 18 DISCHARGE TO SNF
1088847400270 0 0 0 1 ROUTINE/HOME
1088880200270 0 0 0 2 ROUTINE/HOME
1088886900270 0 0 0 1 DISCHARGE HOME WITH HM HLTH SERV
1088927000270 0 0 0 1 DISCHARGE HOME WITH HM HLTH SERV
1089018400270 0 0 0 1 ROUTINE/HOME
1089678200270 0 0 0 20 DISCHARGE HOME WITH HM HLTH SERV
1089910800270 0 0 0 9 DISCHARGE HOME WITH HM HLTH SERV
1090426900270 0 0 0 15 DISCHARGE HOME WITH HM HLTH SERV
1090478300270 0 0 0 1 PATIENT EXPIRED
1092290700270 0 0 0 80 DISCHARGE HOME WITH HM HLTH SERV
1092523600270 0 0 0 3 ROUTINE/HOME
1092588000270 0 0 0 50 DISCHARGE HOME WITH HM HLTH SERV
1093471400270 0 0 0 5 ROUTINE/HOME
1094284500270 0 0 0 12 DISCHARGE TO SNF
1094892300270 0 0 0 13 DISCHARGE TO ACUTE FACILITY
1095101500270 0 0 0 33 ROUTINE/HOME
1095496900270 0 0 0 0 nan
1096386900270 0 0 0 12 ROUTINE/HOME
1096

1161166900270 0 0 0 5 DISCHARGE HOME WITH HM HLTH SERV
1161193900270 0 0 0 10 DISCHARGE HOME WITH HM HLTH SERV
1161515900270 0 0 0 1 ROUTINE/HOME
1161877700270 0 0 0 9 ROUTINE/HOME
1161881700270 0 0 0 23 DISCHARGE TO SNF
1162233200270 0 0 0 6 ROUTINE/HOME
1162665900270 0 0 0 6 DISCHARGE TO SNF
1162939100270 0 0 0 2 DISCHARGE HOME WITH HM HLTH SERV
1163218400270 1 1 1 5 DISCHARGE TO SNF
1163655900270 0 0 0 5 DISCHARGE TO SNF
1163869400270 0 0 0 24 ROUTINE/HOME
1164070700270 0 0 0 3 AGAINST MEDICAL ADVICE
1164218900270 0 0 0 7 ROUTINE/HOME
1164321300270 0 0 0 4 ROUTINE/HOME
1164453800270 0 0 0 11 DISCHARGE HOME WITH HM HLTH SERV
1164863000270 0 0 0 5 DISCHARGE HOME WITH HM HLTH SERV
1164866400270 0 0 0 12 ROUTINE/HOME
1164934900270 0 0 0 2 ROUTINE/HOME
1164940300270 1 1 1 4 ROUTINE/HOME
1165524000270 0 1 1 23 ROUTINE/HOME
1165621700270 0 0 0 4 DISCHARGE HOME WITH HOSPICE
1166417800270 0 0 0 10 ROUTINE/HOME
1166451700270 0 0 0 39 PATIENT EXPIRED
1166599200270 0 0 0 6 DISCHARGE HOME WITH H

In [102]:
cluster=pd.read_excel('/Users/yiyezhang/Dropbox/Grant-and-IRB/AHRQ R03/Analysis/EDDC_order_2012_2018_cluster_MED_task.xlsx', sheetname='EDDC_order_2012_2018_cluster')

generate cluster-specific data for Disco, once you run LCS_clustering.R

In [152]:
#data2: filtered
#data: all
with open(path+'C2_orders_EDDC_HFonly_18_89.csv', 'w') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    combined_row = []
    combined_row.append('pid')
    combined_row.append('date')
    combined_row.append('activity')
    combined_row.append('user')
    writer.writerow(combined_row)
    for pid in data2:
        if  int(pid) in cluster['clientvisitguid'].values:
#             print(pid,cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster']].values[0])
            if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==2:
                for date in data2[pid]['appt']:
                    if len(data2[pid]['appt'][date]['proc'])>0 or len(data2[pid]['appt'][date]['drug'])>0:
                        combined_row = []
                        combined_row.append(pid)
                        #combined_row.append('@')
                        combined_row.append(date)
                        #combined_row.append('@')
                        combined_row.append(str(data[pid]['appt'][date]['diag'])+str(sorted(data2[pid]['appt'][date]['proc']))+str(sorted(data2[pid]['appt'][date]['drugclass'])))
                        combined_row.append(data2[pid]['appt'][date]['user'])
                        writer.writerow(combined_row)
                

In [ ]:
#can skip
for pid in data2:
    os=0
    for date in data2[pid]['appt']:
        if  'Clinical Pathway - Heart Failure Order Set (LMH)' in data2[pid]['appt'][date]['proc'] or 'Clinical Pathway - Heart Failure Order Set' in data2[pid]['appt'][date]['proc'] or  'ED Order set - Dyspnea/CHF/COPD/Asthma (LMH)' in data2[pid]['appt'][date]['proc'] or  'ED Order set - Dyspnea/CHF/COPD/Asthma' in data2[pid]['appt'][date]['proc']:
            os=1
            break
    print(pid,os)  

In [132]:
#common drugs in cluster 2
diaglistC3=[]
for pid in data:
    if  int(pid) in cluster['clientvisitguid'].values:
        if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==3:
            for date in data[pid]['appt']:
                for icd in data[pid]['appt'][date]['diag']:
                    diaglistC3.append(icd)
c=Counter(diaglistC3)
c_most_common = [item for item in c.most_common(20)]

In [133]:
c_most_common

[(nan, 860),
 ('I50.9', 178),
 ('N17.9', 122),
 ('R06.02', 99),
 ('I50.23', 84),
 ('I48.91', 79),
 ('I50.33', 59),
 ('J18.9', 55),
 ('D64.9', 50),
 ('R41.82', 47),
 ('I10', 45),
 ('I25.10', 45),
 ('I50.21', 44),
 ('I34.0', 37),
 ('D72.829', 37),
 ('J96.01', 36),
 ('R06.00', 36),
 ('A41.9', 35),
 ('E11.9', 32),
 ('N39.0', 31)]

In [134]:
orderlistC3=[]
for pid in data:
    if int(pid) in cluster['clientvisitguid'].values:
        if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==3:
            for date in data[pid]['appt']:
                for icd in data[pid]['appt'][date]['proc']:
                    orderlistC3.append(icd)
c=Counter(orderlistC3)
c_most_common = [item for item in c.most_common(20)]

In [135]:
c_most_common

[('OSAM Lab Order Set', 8422),
 ('OSCommonly Used Orders - AM Draw', 7496),
 ('Lab_order', 7097),
 ('12 hour order check up to', 6224),
 ('General Nursing', 1717),
 ('OSCTS AM Labs Order Set', 1603),
 ('OSUrine Lab Order Set', 831),
 ('Indwelling Urinary Catheter (Foley)', 641),
 ('OSMED - ED Admitted Patient Order Set', 580),
 ('Notify MD/NP/PA', 555),
 ('OSHeparin  Drip Order Set (Adult)', 482),
 ('OSED Order Set - A General Comprehensive Order Set', 458),
 ('Nursing Teaching/Counseling', 449),
 ('OSBlood Culture x2', 419),
 ('B/p, hr, rr and temp', 377),
 ('Fingerstick, Glucose', 333),
 ('Cardiac: Fat/Cholesterol Restricted; 2 gm Sodium Diet', 315),
 ('TTE', 285),
 ('Restraints  -', 284),
 ('IV, Peripheral Access', 276)]

In [143]:
druglistC2=[]
for pid in data:
    if  int(pid) in cluster['clientvisitguid'].values:
        if cluster.loc[cluster['clientvisitguid']==int(pid)][['cluster_pull2']].values[0]==2:
            for date in data[pid]['appt']:
                for icd in data[pid]['appt'][date]['drug']:
                    druglistC2.append(icd)


In [148]:
c=Counter(druglistC2)
c_most_common = [item for item in c.most_common(20)]
c_most_common

[('OSAM Lab Order Set', 11883),
 ('Lab_order', 9533),
 ('OSCommonly Used Orders - AM Draw', 8935),
 ('12 hour order check up to', 7516),
 ('OSCTS AM Labs Order Set', 3109),
 ('General Nursing', 2315),
 ('OSUrine Lab Order Set', 1128),
 ('Indwelling Urinary Catheter (Foley)', 928),
 ('OSHeparin  Drip Order Set (Adult)', 881),
 ('OSWarfarin Order Set', 711),
 ('Notify MD/NP/PA', 707),
 ('Renal Replacement Therapy', 612),
 ('OSBlood Culture x2', 601),
 ('Nursing Teaching/Counseling', 476),
 ('Restraints  -', 468),
 ('B/p, hr, rr and temp', 337),
 ('Fingerstick, Glucose', 318),
 ('OSCommonly Used Orders - Now', 318),
 ('B/p, hr', 314),
 ('Hepatitis B Surface Antigen Status', 313)]

In [ ]:
print(len(orderlist),len(orderNotusedbyall))
print(len(druglist),len(drugNotusedbyall))
print(len(diaglist),len(diagNotusedbyall))

below are list for CCW: https://www2.ccwdata.org/web/guest/condition-categories, ask Yufang for code

In [107]:
obesity=['DXE66.01'	,
'E66.09'	,
'E66.1'	,
'E66.2'	,
'E66.8'	,
'E66.9'	,
'Z68.30'	,
'Z68.31'	,
'Z68.32'	,
'Z68.33'	,
'Z68.34'	,
'Z68.35'	,
'Z68.36'	,
'Z68.37'	,
'Z68.38'	,
'Z68.39'	,
'Z68.41'	,
'Z68.42'	,
'Z68.43'	,
'Z68.44'	,
'Z68.45'	,]

In [108]:
depression=['DXF31.30'	,
'F31.31'	,
'F31.32'	,
'F31.4'	,
'F31.5'	,
'F31.60'	,
'F31.61'	,
'F31.62'	,
'F31.63'	,
'F31.64'	,
'F31.75'	,
'F31.76'	,
'F31.77'	,
'F31.78'	,
'F31.81'	,
'F32.0'	,
'F32.1'	,
'F32.2'	,
'F32.3'	,
'F32.4'	,
'F32.5'	,
'F32.9'	,
'F33.0'	,
'F33.1'	,
'F33.2'	,
'F33.3'	,
'F33.40'	,
'F33.41'	,
'F33.42'	,
'F33.8'	,
'F33.9'	,
'F34.1'	,
'F43.21'	,
'F43.23'	]

In [109]:
HTN=['DXH35.031'	,
'H35.032'	,
'H35.033'	,
'H35.039'	,
'I10'	,
'I11.0'	,
'I11.9'	,
'I12.0'	,
'I12.9'	,
'I13.0'	,
'I13.10'	,
'I13.11'	,
'I13.2'	,
'I15.0'	,
'I15.1'	,
'I15.2'	,
'I15.8'	,
'I15.9'	,
'I67.4'	,
'N26.2']

In [110]:
DM=['DXE08.00'	,
'E08.01'	,
'E08.10'	,
'E08.11'	,
'E08.21'	,
'E08.22'	,
'E08.29'	,
'E08.311'	,
'E08.319'	,
'E08.321'	,
'E08.3211'	,
'E08.3212'	,
'E08.3213'	,
'E08.3219'	,
'E08.329'	,
'E08.3291'	,
'E08.3292'	,
'E08.3293'	,
'E08.3299'	,
'E08.331'	,
'E08.3311'	,
'E08.3312'	,
'E08.3313'	,
'E08.3319'	,
'E08.339'	,
'E08.3391'	,
'E08.3392'	,
'E08.3393'	,
'E08.3399'	,
'E08.341'	,
'E08.3411'	,
'E08.3412'	,
'E08.3413'	,
'E08.3419'	,
'E08.349'	,
'E08.3491'	,
'E08.3492'	,
'E08.3493'	,
'E08.3499'	,
'E08.351'	,
'E08.3511'	,
'E08.3512'	,
'E08.3513'	,
'E08.3519'	,
'E08.3521'	,
'E08.3522'	,
'E08.3523'	,
'E08.3529'	,
'E08.3531'	,
'E08.3532'	,
'E08.3533'	,
'E08.3539'	,
'E08.3541'	,
'E08.3542'	,
'E08.3543'	,
'E08.3549'	,
'E08.3551'	,
'E08.3552'	,
'E08.3553'	,
'E08.3559'	,
'E08.359'	,
'E08.3591'	,
'E08.3592'	,
'E08.3593'	,
'E08.3599'	,
'E08.36'	,
'E08.37X1'	,
'E08.37X2'	,
'E08.37X3'	,
'E08.37X9'	,
'E08.39'	,
'E08.40'	,
'E08.41'	,
'E08.42'	,
'E08.43'	,
'E08.44'	,
'E08.49'	,
'E08.51'	,
'E08.52'	,
'E08.59'	,
'E08.610'	,
'E08.618'	,
'E08.620'	,
'E08.621'	,
'E08.622'	,
'E08.628'	,
'E08.630'	,
'E08.638'	,
'E08.641'	,
'E08.649'	,
'E08.65'	,
'E08.69'	,
'E08.8'	,
'E08.9'	,
'E09.00'	,
'E09.01'	,
'E09.10'	,
'E09.11'	,
'E09.21'	,
'E09.22'	,
'E09.29'	,
'E09.311'	,
'E09.319'	,
'E09.321'	,
'E09.3211'	,
'E09.3212'	,
'E09.3213'	,
'E09.3219'	,
'E09.329'	,
'E09.3291'	,
'E09.3292'	,
'E09.3293'	,
'E09.3299'	,
'E09.331'	,
'E09.3311'	,
'E09.3312'	,
'E09.3313'	,
'E09.3319'	,
'E09.339'	,
'E09.3391'	,
'E09.3392'	,
'E09.3393'	,
'E09.3399'	,
'E09.341'	,
'E09.3411'	,
'E09.3412'	,
'E09.3413'	,
'E09.3419'	,
'E09.349'	,
'E09.3491'	,
'E09.3492'	,
'E09.3493'	,
'E09.3499'	,
'E09.351'	,
'E09.3511'	,
'E09.3512'	,
'E09.3513'	,
'E09.3519'	,
'E09.3521'	,
'E09.3522'	,
'E09.3523'	,
'E09.3529'	,
'E09.3531'	,
'E09.3532'	,
'E09.3533'	,
'E09.3539'	,
'E09.3541'	,
'E09.3542'	,
'E09.3543'	,
'E09.3549'	,
'E09.3551'	,
'E09.3552'	,
'E09.3553'	,
'E09.3559'	,
'E09.359'	,
'E09.3591'	,
'E09.3592'	,
'E09.3593'	,
'E09.3599'	,
'E09.36'	,
'E09.37X1'	,
'E09.37X2'	,
'E09.37X3'	,
'E09.37X9'	,
'E09.39'	,
'E09.40'	,
'E09.41'	,
'E09.42'	,
'E09.43'	,
'E09.44'	,
'E09.49'	,
'E09.51'	,
'E09.52'	,
'E09.59'	,
'E09.610'	,
'E09.618'	,
'E09.620'	,
'E09.621'	,
'E09.622'	,
'E09.628'	,
'E09.630'	,
'E09.638'	,
'E09.641'	,
'E09.649'	,
'E09.65'	,
'E09.69'	,
'E09.8'	,
'E09.9'	,
'E10.10'	,
'E10.11'	,
'E10.21'	,
'E10.22'	,
'E10.29'	,
'E10.311'	,
'E10.319'	,
'E10.321'	,
'E10.3211'	,
'E10.3212'	,
'E10.3213'	,
'E10.3219'	,
'E10.329'	,
'E10.3291'	,
'E10.3292'	,
'E10.3293'	,
'E10.3299'	,
'E10.331'	,
'E10.3311'	,
'E10.3312'	,
'E10.3313'	,
'E10.3319'	,
'E10.339'	,
'E10.3391'	,
'E10.3392'	,
'E10.3393'	,
'E10.3399'	,
'E10.341'	,
'E10.3411'	,
'E10.3412'	,
'E10.3413'	,
'E10.3419'	,
'E10.349'	,
'E10.3491'	,
'E10.3492'	,
'E10.3493'	,
'E10.3499'	,
'E10.351'	,
'E10.3511'	,
'E10.3512'	,
'E10.3513'	,
'E10.3519'	,
'E10.359'	,
'E10.36'	,
'E10.37X1'	,
'E10.37X2'	,
'E10.37X3'	,
'E10.37X9'	,
'E10.39'	,
'E10.40'	,
'E10.41'	,
'E10.42'	,
'E10.43'	,
'E10.44'	,
'E10.49'	,
'E10.51'	,
'E10.52'	,
'E10.59'	,
'E10.610'	,
'E10.618'	,
'E10.620'	,
'E10.621'	,
'E10.622'	,
'E10.628'	,
'E10.630'	,
'E10.638'	,
'E10.641'	,
'E10.649'	,
'E10.65'	,
'E10.69'	,
'E10.8'	,
'E10.9'	,
'E11.00'	,
'E11.01'	,
'E11.10'	,
'E11.11'	,
'E11.21'	,
'E11.22'	,
'E11.29'	,
'E11.311'	,
'E11.319'	,
'E11.321'	,
'E11.3211'	,
'E11.3212'	,
'E11.3213'	,
'E11.3219'	,
'E11.329'	,
'E11.3291'	,
'E11.3292'	,
'E11.3293'	,
'E11.3299'	,
'E11.331'	,
'E11.3311'	,
'E11.3312'	,
'E11.3313'	,
'E11.3319'	,
'E11.339'	,
'E11.3391'	,
'E11.3392'	,
'E11.3393'	,
'E11.3399'	,
'E11.341'	,
'E11.3411'	,
'E11.3412'	,
'E11.3413'	,
'E11.3419'	,
'E11.349'	,
'E11.3491'	,
'E11.3492'	,
'E11.3493'	,
'E11.3499'	,
'E11.351'	,
'E11.3511'	,
'E11.3512'	,
'E11.3513'	,
'E11.3519'	,
'E11.3521'	,
'E11.3522'	,
'E11.3523'	,
'E11.3529'	,
'E11.3531'	,
'E11.3532'	,
'E11.3533'	,
'E11.3539'	,
'E11.3541'	,
'E11.3542'	,
'E11.3543'	,
'E11.3549'	,
'E11.3551'	,
'E11.3552'	,
'E11.3553'	,
'E11.3559'	,
'E11.359'	,
'E11.3591'	,
'E11.3592'	,
'E11.3593'	,
'E11.3599'	,
'E11.36'	,
'E11.37X1'	,
'E11.37X2'	,
'E11.37X3'	,
'E11.37X9'	,
'E11.39'	,
'E11.40'	,
'E11.41'	,
'E11.42'	,
'E11.43'	,
'E11.44'	,
'E11.49'	,
'E11.51'	,
'E11.52'	,
'E11.59'	,
'E11.610'	,
'E11.618'	,
'E11.620'	,
'E11.621'	,
'E11.622'	,
'E11.628'	,
'E11.630'	,
'E11.638'	,
'E11.641'	,
'E11.649'	,
'E11.65'	,
'E11.69'	,
'E11.8'	,
'E11.9'	,
'E13.00'	,
'E13.01'	,
'E13.10'	,
'E13.11'	,
'E13.21'	,
'E13.22'	,
'E13.29'	,
'E13.311'	,
'E13.319'	,
'E13.321'	,
'E13.3211'	,
'E13.3212'	,
'E13.3213'	,
'E13.3219'	,
'E13.329'	,
'E13.3291'	,
'E13.3292'	,
'E13.3293'	,
'E13.3299'	,
'E13.331'	,
'E13.3311'	,
'E13.3312'	,
'E13.3313'	,
'E13.3319'	,
'E13.339'	,
'E13.3391'	,
'E13.3392'	,
'E13.3393'	,
'E13.3399'	,
'E13.341'	,
'E13.3411'	,
'E13.3412'	,
'E13.3413'	,
'E13.3419'	,
'E13.349'	,
'E13.3491'	,
'E13.3492'	,
'E13.3493'	,
'E13.3499'	,
'E13.351'	,
'E13.3511'	,
'E13.3512'	,
'E13.3513'	,
'E13.3519'	,
'E13.3521'	,
'E13.3522'	,
'E13.3523'	,
'E13.3529'	,
'E13.3531'	,
'E13.3532'	,
'E13.3533'	,
'E13.3539'	,
'E13.3541'	,
'E13.3542'	,
'E13.3543'	,
'E13.3549'	,
'E13.3551'	,
'E13.3552'	,
'E13.3553'	,
'E13.3559'	,
'E13.359'	,
'E13.36'	,
'E13.39'	,
'E13.40'	,
'E13.41'	,
'E13.42'	,
'E13.43'	,
'E13.44'	,
'E13.49'	,
'E13.51'	,
'E13.52'	,
'E13.59'	,
'E13.610'	,
'E13.618'	,
'E13.620'	,
'E13.621'	,
'E13.622'	,
'E13.628'	,
'E13.630'	,
'E13.638'	,
'E13.641'	,
'E13.649'	,
'E13.65'	,
'E13.69'	,
'E13.8'	,
'E13.9']

In [111]:
Ischemic=['DXI20.0'	,
'I20.1'	,
'I20.8'	,
'I20.9'	,
'I21.01'	,
'I21.02'	,
'I21.09'	,
'I21.11'	,
'I21.19'	,
'I21.21'	,
'I21.29'	,
'I21.3'	,
'I21.4'	,
'I21.A1'	,
'I21.A9'	,
'I22.0'	,
'I22.1'	,
'I22.2'	,
'I22.8'	,
'I22.9'	,
'I23.0'	,
'I23.1'	,
'I23.2'	,
'I23.3'	,
'I23.4'	,
'I23.5'	,
'I23.6'	,
'I23.7'	,
'I23.8'	,
'I24.0'	,
'I24.1'	,
'I24.8'	,
'I24.9'	,
'I25.10'	,
'I25.110'	,
'I25.111'	,
'I25.118'	,
'I25.119'	,
'I25.2'	,
'I25.3'	,
'I25.41'	,
'I25.42'	,
'I25.5'	,
'I25.6'	,
'I25.700'	,
'I25.701'	,
'I25.708'	,
'I25.709'	,
'I25.710'	,
'I25.711'	,
'I25.718'	,
'I25.719'	,
'I25.720'	,
'I25.721'	,
'I25.728'	,
'I25.729'	,
'I25.730'	,
'I25.731'	,
'I25.738'	,
'I25.739'	,
'I25.750'	,
'I25.751'	,
'I25.758'	,
'I25.759'	,
'I25.760'	,
'I25.761'	,
'I25.768'	,
'I25.769'	,
'I25.790'	,
'I25.791'	,
'I25.798'	,
'I25.799'	,
'I25.810'	,
'I25.811'	,
'I25.812'	,
'I25.82'	,
'I25.83'	,
'I25.84'	,
'I25.89'	,
'I25.9']

In [112]:
Afib=['DXI48.0'	,
'I48.1'	,
'I48.2'	,
'I48.91'	]

In [113]:
CKD=['DXA18.11'	,
'A52.75'	,
'B52.0'	,
'C64.1'	,
'C64.2'	,
'C64.9'	,
'C68.9'	,
'D30.00'	,
'D30.01'	,
'D30.02'	,
'D41.00'	,
'D41.01'	,
'D41.02'	,
'D41.10'	,
'D41.11'	,
'D41.12'	,
'D41.20'	,
'D41.21'	,
'D41.22'	,
'D59.3'	,
'E08.21'	,
'E08.22'	,
'E08.29'	,
'E08.65'	,
'E09.21'	,
'E09.22'	,
'E09.29'	,
'E10.21'	,
'E10.22'	,
'E10.29'	,
'E10.65'	,
'E11.21'	,
'E11.22'	,
'E11.29'	,
'E11.65'	,
'E13.21'	,
'E13.22'	,
'E13.29'	,
'E74.8'	,
'I12.0'	,
'I12.9'	,
'I13.0'	,
'I13.10'	,
'I13.11'	,
'I13.2'	,
'I70.1'	,
'I72.2'	,
'K76.7'	,
'M10.30'	,
'M10.311'	,
'M10.312'	,
'M10.319'	,
'M10.321'	,
'M10.322'	,
'M10.329'	,
'M10.331'	,
'M10.332'	,
'M10.339'	,
'M10.341'	,
'M10.342'	,
'M10.349'	,
'M10.351'	,
'M10.352'	,
'M10.359'	,
'M10.361'	,
'M10.362'	,
'M10.369'	,
'M10.371'	,
'M10.372'	,
'M10.379'	,
'M10.38'	,
'M10.39'	,
'M32.14'	,
'M32.15'	,
'M35.04'	,
'N00.0'	,
'N00.1'	,
'N00.2'	,
'N00.3'	,
'N00.4'	,
'N00.5'	,
'N00.6'	,
'N00.7'	,
'N00.8'	,
'N00.9'	,
'N01.0'	,
'N01.1'	,
'N01.2'	,
'N01.3'	,
'N01.4'	,
'N01.5'	,
'N01.6'	,
'N01.7'	,
'N01.8'	,
'N01.9'	,
'N02.0'	,
'N02.1'	,
'N02.2'	,
'N02.3'	,
'N02.4'	,
'N02.5'	,
'N02.6'	,
'N02.7'	,
'N02.8'	,
'N02.9'	,
'N03.0'	,
'N03.1'	,
'N03.2'	,
'N03.3'	,
'N03.4'	,
'N03.5'	,
'N03.6'	,
'N03.7'	,
'N03.8'	,
'N03.9'	,
'N04.0'	,
'N04.1'	,
'N04.2'	,
'N04.3'	,
'N04.4'	,
'N04.5'	,
'N04.6'	,
'N04.7'	,
'N04.8'	,
'N04.9'	,
'N05.0'	,
'N05.1'	,
'N05.2'	,
'N05.3'	,
'N05.4'	,
'N05.5'	,
'N05.6'	,
'N05.7'	,
'N05.8'	,
'N05.9'	,
'N06.0'	,
'N06.1'	,
'N06.2'	,
'N06.3'	,
'N06.4'	,
'N06.5'	,
'N06.6'	,
'N06.7'	,
'N06.8'	,
'N06.9'	,
'N07.0'	,
'N07.1'	,
'N07.2'	,
'N07.3'	,
'N07.4'	,
'N07.5'	,
'N07.6'	,
'N07.7'	,
'N07.8'	,
'N07.9'	,
'N08'	,
'N13.1'	,
'N13.2'	,
'N13.30'	,
'N13.39'	,
'N14.0'	,
'N14.1'	,
'N14.2'	,
'N14.3'	,
'N14.4'	,
'N15.0'	,
'N15.8'	,
'N15.9'	,
'N16'	,
'N17.0'	,
'N17.1'	,
'N17.2'	,
'N17.8'	,
'N17.9'	,
'N18.1'	,
'N18.2'	,
'N18.3'	,
'N18.4'	,
'N18.5'	,
'N18.6'	,
'N18.9'	,
'N19'	,
'N25.0'	,
'N25.1'	,
'N25.81'	,
'N25.89'	,
'N25.9'	,
'N26.1'	,
'N26.9'	,
'Q61.02'	,
'Q61.11'	,
'Q61.19'	,
'Q61.2'	,
'Q61.3'	,
'Q61.4'	,
'Q61.5'	,
'Q61.8'	,
'Q62.0'	,
'Q62.2'	,
'Q62.10'	,
'Q62.11'	,
'Q62.12'	,
'Q62.31'	,
'Q62.32'	,
'Q62.39'	,
'R94.4'	]

In [114]:
COPD=['DXJ40'	,
'J41.0'	,
'J41.1'	,
'J41.8'	,
'J42'	,
'J43.0'	,
'J43.1'	,
'J43.2'	,
'J43.8'	,
'J43.9'	,
'J44.0'	,
'J44.1'	,
'J44.9'	,
'J47.0'	,
'J47.1'	,
'J47.9'	]

In [115]:
CCW={}
for pid in data:
    CCW[pid]={}
    CCW[pid]['score']=0
    if len(data[pid]['appt']) != 0:
        for date in data[pid]['appt']:
            for i in data[pid]['appt'][date]['diag']:
                if i in CKD:
                    if 'CKD' not in CCW[pid]:
                        CCW[pid]['CKD']=1
                if i in obesity:
                    if 'obesity' not in CCW[pid]:
                        CCW[pid]['obesity']=1
                if i in depression:
                    if 'depression' not in CCW[pid]:
                        CCW[pid]['depression']=1
                if i in HTN:
                    if 'HTN' not in CCW[pid]:
                        CCW[pid]['HTN']=1
                if i in DM:
                    if 'DM' not in CCW[pid]:
                        CCW[pid]['DM']=1
                if i in Ischemic:
                    if 'Ischemic' not in CCW[pid]:
                        CCW[pid]['Ischemic']=1
                if i in Afib:
                    if 'Afib' not in CCW[pid]:
                        CCW[pid]['Afib']=1
                if i in COPD:
                    if 'COPD' not in CCW[pid]:
                        CCW[pid]['COPD']=1
for pid in CCW:
    for item in CCW[pid]:
        CCW[pid]['score']=CCW[pid][item]+CCW[pid]['score']

In [116]:
for pid in CCW:
    print (pid,CCW[pid]['score'])

556943700270 1
561002000270 0
562000000270 0
567313100270 3
579333200270 2
582002300270 3
584744300270 1
608150700270 1
624731800270 5
624817200270 1
653284000270 2
684111000270 0
685155700270 1
685526500270 0
737643900270 2
763338100270 1
763976700270 1
766032300270 1
768628200270 3
771224000270 2
774599200270 1
778172900270 0
778912000270 2
781162000270 3
786831400270 0
787961400270 2
789394000270 2
789853200270 2
790112500270 2
790635800270 0
790857300270 4
791127000270 2
791130400270 2
791560800270 1
791730100270 3
791835100270 5
792864300270 0
792925100270 3
793140600270 1
793251400270 2
793451300270 2
793475600270 2
793791700270 3
794515700270 4
795313200270 1
795395900270 1
795789100270 1
796870000270 1
797101000270 2
797148000270 2
797168300270 1
797214500270 4
797223000270 3
797234500270 1
797484600270 2
797534000270 4
798001600270 2
798714100270 3
799591100270 4
799604300270 2
799618900270 0
800196300270 3
800566900270 4
801095100270 1
801550000270 2
802079000270 0
8020953002

1026864700270 0
1026925700270 2
1027466500270 2
1027607500270 1
1028844000270 3
1029125900270 4
1029341600270 0
1029597200270 2
1030300200270 1
1030395100270 0
1030597400270 0
1030854800270 2
1031112000270 1
1031323300270 2
1031383900270 1
1031544300270 1
1031574300270 0
1031633400270 2
1031644100270 0
1031896200270 1
1032182300270 1
1032645700270 1
1032759300270 1
1032932200270 0
1033156800270 4
1033294400270 1
1033333600270 1
1033434400270 4
1033542500270 0
1034344100270 1
1034380300270 2
1034413400270 1
1034661100270 4
1034943900270 2
1034951500270 0
1035050600270 0
1035284600270 2
1035384300270 3
1035419100270 0
1035882400270 3
1036035900270 1
1036071700270 4
1036577900270 2
1037061700270 2
1037154400270 1
1037155800270 4
1037175700270 3
1037220100270 3
1037248400270 5
1037593900270 5
1038153600270 3
1038265900270 0
1038565400270 1
1038578700270 2
1039750600270 0
1039761700270 1
1039777600270 2
1039887000270 1
1040071000270 2
1040447500270 0
1041000800270 3
1041465600270 2
10415055

1254562500270 0
1254579600270 0
1254636200270 1
1254948100270 3
1256154500270 2
1257528700270 1
1257579500270 2
1257904300270 1
1258266900270 2
1258335100270 2
1258763000270 4
1259030500270 2
1259267100270 0
1259325200270 1
1259587100270 1
1259709100270 2
1260233900270 5
1260567600270 0
1260570500270 1
1260933100270 1
1261003500270 2
1261274500270 0
1261373800270 1
1261566300270 1
1261803900270 0
1261889000270 1
1262538100270 1
1262686400270 3
1262745700270 3
1263124200270 2
1263746900270 0
1264106000270 3
1264531800270 0
1264853300270 1
1264870700270 1
1264963300270 0
1265170900270 1
1265595100270 2
1265609400270 0
1265701200270 0
1265725000270 1
1265985500270 1
1266342500270 4
1267697800270 5
1267842000270 1
1267862900270 2
1267876400270 2
1267903500270 3
1268141600270 5
1268682700270 1
1268912600270 2
1269084300270 1
1270810600270 1
1271511400270 2
1271703900270 2
1271734400270 1
1271803700270 2
1272344700270 4
1272408600270 1
1273735100270 2
1273899200270 3
1274504100270 2
12746647

In [117]:
len(CCW)

1651

In [118]:
for pid in data:
    VTE=0
    for date in data[pid]['appt']:
        for icd in data[pid]['appt'][date]['diag']:
            if isinstance(icd, float)==False:
                if icd[0:3]=='I82':
                    VTE=1
                    break
    print(pid,VTE)

556943700270 0
561002000270 0
562000000270 0
567313100270 1
579333200270 0
582002300270 0
584744300270 0
608150700270 0
624731800270 0
624817200270 0
653284000270 0
684111000270 0
685155700270 0
685526500270 1
737643900270 0
763338100270 0
763976700270 0
766032300270 0
768628200270 0
771224000270 1
774599200270 0
778172900270 0
778912000270 0
781162000270 0
786831400270 1
787961400270 0
789394000270 0
789853200270 0
790112500270 0
790635800270 0
790857300270 0
791127000270 0
791130400270 0
791560800270 0
791730100270 0
791835100270 0
792864300270 0
792925100270 0
793140600270 0
793251400270 0
793451300270 0
793475600270 0
793791700270 0
794515700270 0
795313200270 0
795395900270 0
795789100270 0
796870000270 0
797101000270 0
797148000270 0
797168300270 0
797214500270 0
797223000270 0
797234500270 0
797484600270 0
797534000270 0
798001600270 0
798714100270 0
799591100270 0
799604300270 0
799618900270 0
800196300270 1
800566900270 0
801095100270 0
801550000270 0
802079000270 0
8020953002

979833800270 0
979923900270 0
980065400270 0
980304600270 0
980975300270 0
981328000270 0
981556400270 0
981677900270 0
981699700270 0
982001500270 0
982259300270 0
982649000270 0
983404800270 0
983527700270 0
983544700270 0
983616700270 0
983688400270 1
984201000270 0
984724000270 0
984736200270 0
984959300270 0
985771200270 0
986601800270 0
986814600270 0
986881800270 0
987161900270 0
987269900270 0
987295600270 0
987386000270 0
987959800270 0
988560400270 0
988937500270 0
989516100270 0
989563600270 0
989604800270 0
989839800270 0
989875400270 0
989979500270 0
991193100270 0
991212100270 0
991725300270 0
992160100270 0
992171800270 0
992214000270 0
992239900270 0
992240900270 0
992565500270 0
993101900270 0
993249100270 0
993888500270 0
994050900270 0
994075500270 0
994343100270 0
994368200270 1
994830700270 0
994909800270 0
995730400270 0
996043000270 0
996193000270 0
996352600270 0
996405100270 0
996575000270 0
997044900270 0
997296900270 1
997544200270 0
997602600270 0
9976822002

1157687100270 0
1157974600270 0
1158988800270 1
1159085700270 0
1160703100270 0
1161153600270 0
1161166900270 0
1161193900270 0
1161515900270 0
1161877700270 0
1161881700270 0
1162233200270 0
1162665900270 0
1162939100270 0
1163218400270 0
1163655900270 0
1163869400270 0
1164070700270 0
1164218900270 0
1164321300270 0
1164453800270 0
1164863000270 0
1164866400270 0
1164934900270 0
1164940300270 0
1165524000270 0
1165621700270 0
1166417800270 0
1166451700270 0
1166599200270 0
1167241700270 0
1168403200270 0
1168425500270 0
1168430500270 0
1168493200270 0
1169128300270 0
1169417900270 0
1169719000270 0
1170061900270 1
1170806400270 0
1170830800270 0
1170966600270 0
1170983100270 0
1171183100270 0
1171315600270 0
1171950100270 0
1172050300270 0
1172123300270 0
1172149300270 0
1172224500270 0
1172290100270 0
1172661200270 0
1173485600270 0
1173734500270 0
1173769300270 0
1173777100270 0
1174110500270 0
1174192100270 0
1174204400270 0
1174359300270 0
1174466000270 0
1175183600270 0
11757722

In [100]:
for pid in data2:
    if pid=='967421600270':
        print(data2[pid])

{'admittime': '2017-01-17 19:00:00', 'age': 1946, 'appt': {'2017-01-17 11:00:00': {'diag': [], 'drug': [], 'lab': [], 'location': ['Adult ED', 'WR-EVAL', 'AWR'], 'proc': [], 'type': 'I', 'user': [], 'drugclass': []}, '2017-01-17 12:00:00': {'diag': [], 'drug': [], 'lab': [], 'location': ['HALLA09'], 'proc': ['OSED Order Set - A General Comprehensive Order Set'], 'type': 'I', 'user': [], 'drugclass': []}, '2017-01-17 13:00:00': {'diag': [], 'drug': [], 'lab': [], 'location': ['HALLA09', 'HALLA09'], 'proc': [], 'type': 'I', 'user': ['Q3'], 'drugclass': ['Furosemide']}, '2017-01-17 17:00:00': {'diag': [], 'drug': [], 'lab': [], 'location': ['HALLA09', 'HALLA09'], 'proc': [], 'type': 'I', 'user': [], 'drugclass': []}, '2017-01-17 20:00:00': {'diag': [], 'drug': [], 'lab': [], 'location': ['EDIA-EDIA*-04', 'EDIA-EDIA*-04'], 'proc': [], 'type': 'I', 'user': [], 'drugclass': []}, '2017-01-17 22:00:00': {'diag': [], 'drug': [], 'lab': [], 'location': ['EDIA-EDIA*-04', 'EDIA-EDIA*-04'], 'proc':

In [122]:
for pid in data2:
    for date in data2[pid]['appt']:
        age = int(date[0:4])-data2[pid]['age']
        print(pid, age)

556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
556943700270 79
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
561002000270 80
56100200

624817200270 70
624817200270 70
624817200270 70
624817200270 70
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
653284000270 85
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
684111000270 47
68411100

763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
763338100270 67
76333810

771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
771224000270 67
77122400

786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
786831400270 82
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
787961400270 65
78796140

...

1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 61
1260933100270 

1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 81
1262538100270 

1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1266342500270 81
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 79
1267697800270 

1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 62
1271703900270 

1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279481500270 66
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1279949200270 83
1281548600270 77
1281548600270 77
1281548600270 77
1281548600270 77
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1281548600270 79
1282144100270 66
1282144100270 